In [85]:
!pip install dgl -f https://data.dgl.ai/wheels/torch-2.4/repo.html
!pip install matgl

import matgl
matgl.set_backend("DGL")

Looking in links: https://data.dgl.ai/wheels/torch-2.4/repo.html


In [2]:
from pymatgen.core import Lattice, Structure

model = matgl.load_model("MEGNet-MP-2018.6.1-Eform")

# This is the structure obtained from the Materials Project.
struct = Structure.from_spacegroup("Pm-3m", Lattice.cubic(4.1437), ["Cs", "Cl"], [[0, 0, 0], [0.5, 0.5, 0.5]])
eform = model.predict_structure(struct)
print(f"The predicted formation energy for CsCl is {float(eform.numpy()):.3f} eV/atom.")

DGL backend not selected or invalid.  Assuming PyTorch for now.


Setting the default backend to "pytorch". You can change it in the ~/.dgl/config.json file or export the DGLBACKEND environment variable.  Valid options are: pytorch, mxnet, tensorflow (all lowercase)
The predicted formation energy for CsCl is -2.272 eV/atom.


/usr/local/lib/python3.12/dist-packages/matgl/utils/io.py:159: UserWarning: Incompatible model version detected! The code will continue to load the model but it is recommended that you provide a path to an updated model, increment your @model_version in model.json if you are confident that the changes are not problematic, or clear your ~/.matgl cache using `python -c "import matgl; matgl.clear_cache()"`
  _check_ver(cls_, v)  # Check version of any subclasses too.
/usr/local/lib/python3.12/dist-packages/dgl/readout.py:443: DGLWarning: For a single graph, use a tensor of shape (1, *) for graph_feat. The support of shape (*) will be deprecated.
  dgl_warning(


In [3]:
#!pip install "numpy<2"
#!pip install dgl==2.2.0
#!pip install torch==2.3.0
#!pip install "torchdata<=0.8.0"
!pip install xgboost
!pip install catboost
#!pip install matgl

   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 99.2/99.2 MB 8.0 MB/s eta 0:00:00


In [4]:
import torch
from pymatgen.core import Lattice, Structure

struct = Structure.from_spacegroup("Pm-3m", Lattice.cubic(4.1437), ["Cs", "Cl"], [[0, 0, 0], [0.5, 0.5, 0.5]])
model = matgl.load_model("MEGNet-MP-2019.4.1-BandGap-mfi")

In [5]:
# Load the pre-trained M3GNet formation energy model
model = matgl.load_model("M3GNet-MP-2018.6.1-Eform")
eform = model.predict_structure(struct)
print(f"The predicted formation energy for CsCl is {float(eform):.3f} eV/atom.")

# Extract the structure features of a structure
feat_dict = model.model.predict_structure(struct, return_features=True)
# Print out structure-wise features, it should be the dimension of node_features * 2 from set2set layer
print(feat_dict["readout"].shape)



The predicted formation energy for CsCl is -2.220 eV/atom.
torch.Size([1, 128])


In [1]:
import pandas as pd
import numpy as np
import plotly as pt
import seaborn as sns
#!pip install pymatgen
!pip install mp_api
import requests
import json
import matplotlib.pyplot as plt
!pip install matminer

  Using cached matminer-0.9.3-py3-none-any.whl.metadata (4.9 kB)
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 5.5/5.5 MB 32.8 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 1.7/1.7 MB 19.2 MB/s eta 0:00:00
   ━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━━ 331.1/331.1 kB 12.7 MB/s eta 0:00:00


#Initialization

In [199]:
extract_CIFs = False
cif_folder = "/content/drive/MyDrive/University/Artificial intelligence in chemistry/Perovskite project/Perovskite-liked-oxides-bandgap-prediction/Data/CIF/"

remove_outliers = True
remove_outliers_manually = True
remove_outliers_after_descriptors = False

update_IDs = False  #request material IDs from databases
target_col = 'Log_rate'
cross_validation = True
dataset_from_google_drive = True
grid_search = False
do_PCA = False
do_PCA_on_embeddings_only = True
do_LASSO = True
finite_log_of_zero_rate = False
embedding_type = 'RDF' #   'None',  'SiteStatsFingerprint' , 'M3GNet', 'RDF', 'CGCNN', 'electronic_RDF'

do_augmentation = False

In [200]:

df = None
if(dataset_from_google_drive):
  df = pd.read_excel("/content/drive/MyDrive/University/Artificial intelligence in chemistry/Perovskite project/Perovskite-liked-oxides-bandgap-prediction/Data/Perovskite dataset export.xlsx",sheet_name='Photocatalytic dataset')
else:
  df = pd.read_excel("dataset.xlsx")

In [201]:
df

Perovskite   Hill formula Interlayer space composition  Bandgap, eV  \
0       K4Nb6O17     K4 Nb6 O17                          NaN         3.50   
1       KLaNb2O7    K La Nb2 O7                          NaN         3.20   
2      RbLaNb2O7   La Nb2 O7 Rb                          NaN         3.35   
3      CsLaNb2O7   Cs La Nb2 O7                          NaN         3.30   
4     KCa2Nb3O10  Ca2 K Nb3 O10                          NaN         3.35   
...          ...            ...                          ...          ...   
1084        TiO2            NaN                          NaN         3.20   
1085        TiO2            NaN                          NaN         3.20   
1086        TiO2            NaN                          NaN         3.20   
1087        TiO2            NaN                          NaN         3.20   
1088        TiO2            NaN                          NaN         3.20   

                            DOI Materials Project ID   COD_ID Springer_ID  \
0            10.1007/BF00765319            mp-560692  1001842         NaN   
1            10.1007/BF00765319           mp-1223501  1545643         NaN   
2            10.1007/BF00765319            mp-553965       -1         NaN   
3            10.1007/BF00765319            mp-553248  2004917         NaN   
4            10.1007/BF00765319            mp-557195  1521061         NaN   
...                         ...                  ...      ...         ...   
1084  10.1134/S107036321404001X           mp-1245098  1010942         NaN   
1085  10.1134/S107036321404001X           mp-1245098  1010942         NaN   
1086  10.1134/S107036321404001X           mp-1245098  1010942         NaN   
1087  10.1134/S107036321404001X           mp-1245098  1010942         NaN   
1088  10.1134/S107036321404001X           mp-1245098  1010942         NaN   

     MP_CIF_modifier COD_CIF_modifier  ... CatW, g/L  Alcohol, %  Sac Agent 1  \
0                NaN              NaN  ...      2.85        14.3            -   
1                NaN              NaN  ...      2.85        14.3            -   
2                NaN              NaN  ...      2.85        14.3            -   
3                NaN              NaN  ...      2.85        14.3            -   
4                NaN              NaN  ...      2.85        14.3            -   
...              ...              ...  ...       ...         ...          ...   
1084             NaN              NaN  ...      1.00         0.1            -   
1085             NaN              NaN  ...      1.00         0.1            -   
1086             NaN              NaN  ...      1.00         0.1            -   
1087             NaN              NaN  ...      1.00         0.1            -   
1088             NaN              NaN  ...      1.00         0.1            -   

      Sac agent 2  Light type Power, W Wave length min, nm Cell material  \
0               -     Hg lamp    450.0                 NaN           NaN   
1               -     Hg lamp    450.0                 NaN           NaN   
2               -     Hg lamp    450.0                 NaN           NaN   
3               -     Hg lamp    450.0                 NaN           NaN   
4               -     Hg lamp    450.0                 NaN           NaN   
...           ...         ...      ...                 ...           ...   
1084            -     Hg lamp    125.0               220.0        quartz   
1085            -     Hg lamp    125.0               220.0        quartz   
1086            -     Hg lamp    125.0               220.0        quartz   
1087            -     Hg lamp    125.0               220.0        quartz   
1088            -     Hg lamp    125.0               220.0        quartz   

      Temperature, K  Rate, umol/(g*h)  
0                NaN        130.000000  
1                NaN         28.000000  
2                NaN         60.000000  
3                NaN         12.000000  
4                NaN         14.000000  
...              ...    

In [202]:
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1089 entries, 0 to 1088
Data columns (total 88 columns):
 #   Column                                Non-Null Count  Dtype  
---  ------                                --------------  -----  
 0   Perovskite                            1089 non-null   object 
 1   Hill formula                          730 non-null    object 
 2   Interlayer space composition          5 non-null      object 
 3   Bandgap, eV                           1054 non-null   float64
 4   DOI                                   1084 non-null   object 
 5   Materials Project ID                  1058 non-null   object 
 6   COD_ID                                935 non-null    object 
 7   Springer_ID                           257 non-null    object 
 8   MP_CIF_modifier                       510 non-null    object 
 9   COD_CIF_modifier                      197 non-null    object 
 10  Springer_CIF_modifier                 121 non-null    object 
 11  Materials Project

In [203]:
df.describe()

Bandgap, eV           Z        Z_MP       Z_COD  Z_Springer  \
count  1054.000000  694.000000  832.000000  836.000000  836.000000   
mean      3.313241    2.275216    1.260817    1.281100    0.151715   
std       0.644047    1.762830    3.460696    2.116075    0.642689   
min       0.010000    0.333333    0.000000    0.000000    0.000000   
25%       3.100000    1.000000    0.000000    0.000000    0.000000   
50%       3.410000    2.000000    0.000000    0.000000    0.000000   
75%       3.600000    4.000000    1.000000    2.000000    0.000000   
max       5.500000   16.000000   50.000000   16.000000    4.000000   

              d,A        a_MP        b_MP        c_MP       a_COD  ...  \
count  810.000000  827.000000  354.000000  354.000000  832.000000  ...   
mean    14.386401    3.084536    7.406617   14.790353    3.040421  ...   
std      7.950408    4.236046    3.399894    8.264087    6.154639  ...   
min      0.000000    0.000000    3.840000    3.904344    0.000000  ...   
25%     11.185000    0.000000    3.950634   10.502783    0.000000  ...   
50%     14.733000    0.000000    7.415443   12.879040    0.000000  ...   
75%     17.850000    5.801718    7.938952   15.513552    3.899000  ...   
max     38.670000   22.855297   20.551678   48.809404   41.857000  ...   

       Oxygen_concentration avg  Packing fraction avg     CalcT(K)  \
count                832.000000            832.000000  1010.000000   
mean                        inf              0.238767  1287.020792   
std                         NaN              0.257556   222.542464   
min                    0.000000              0.000000   453.000000   
25%                    0.037279              0.000000  1223.000000   
50%                    0.042938              0.000000  1373.000000   
75%                    0.046684              0.533675  1423.000000   
max                         inf              0.657822  1873.000000   

       Calc time (h)   CatW, g/L  Alcohol, %     Power, W  \
count     973.000000  987.000000  966.000000   994.000000   
mean       19.338386    1.428618    5.628230   306.726358   
std        25.264723    1.324191    8.781436   198.606250   
min         0.000000    0.000000    0.000000   100.000000   
25%        10.000000    0.500000    0.000000   125.000000   
50%        12.000000    1.000000    1.000000   300.000000   
75%        24.000000    2.000000   10.000000   450.000000   
max       200.000000   10.000000   90.000000  1000.000000   

       Wave length min, nm  Temperature, K  Rate, umol/(g*h)  
count           689.000000      540.000000        989.000000  
mean            288.388970      294.435185       6914.999659  
std              88.814702       13.175195      21648.175384  
min             200.000000      288.000000          0.000000  
25%             220.000000      288.000000         15.500000  
50%             220.000000      288.000000        166.000000  
75%             400.000000      293.000000       1680.000000  
max             660.000000      333.000000     156000.000000  

[8 rows x 55 columns]

In [204]:
df.columns

Index(['Perovskite', 'Hill formula', 'Interlayer space composition',
       'Bandgap, eV', 'DOI', 'Materials Project ID', 'COD_ID', 'Springer_ID',
       'MP_CIF_modifier', 'COD_CIF_modifier', 'Springer_CIF_modifier',
       'Materials Project verification', 'COD verification',
       'Springer verification', 'General verification', 'MP_CIF_modified',
       'COD_CIF_modified', 'Springer_CIF_modified', 'Z', 'Z_MP', 'Z_COD',
       'Z_Springer', 'a, A', 'b, A', 'c, A', 'Symmetry group', 'd,A', 'a_MP',
       'b_MP', 'c_MP', 'a_COD', 'b_COD', 'c_COD', 'a_Springer', 'b_Springer',
       'c_Springer', 'Number of octahedrons on a layer', 'Valence electrons',
       'Volume', 'Volume_MP', 'Volume_COD', 'Volume_Springer',
       'Valence Electrons Density', 'Valence Electrons Density_MP',
       'Valence Electrons Density_COD', 'Springer_Valence Electrons Density',
       'avg s valence electrons', 'avg p valence electrons',
       'avg d valence electrons', 'avg f valence electrons',
       

In [205]:
init_columns = ['Perovskite', 'Interlayer space composition',
       'Bandgap, eV', 'Materials Project ID', 'COD_ID', 'Springer_ID',
       'Z', 'a, A', 'b, A', 'c, A',
       'Symmetry group', 'd,A',
       'Number of octahedrons on a layer', 'Prep Method', 'CalcT(K)', 'Calc time (h)',
       'Nitrogen', 'Promotion method', 'Promoter', 'Promoter, w%',
       'Surface area, m2/g', 'CatW, g/L', 'Alcohol, %', 'Sac Agent 1',
       'Sac agent 2', 'Light type', 'Power, W', 'Wave length min, nm',
       'Cell material', 'Temperature, K', 'Rate, umol/(g*h)']

init_columns = init_columns + ['MP_CIF_modifier', 'COD_CIF_modifier', 'Springer_CIF_modifier',
       'Materials Project verification', 'COD verification',
       'Springer verification', 'General verification', 'MP_CIF_modified',
       'COD_CIF_modified', 'Springer_CIF_modified']
print(init_columns)

['Perovskite', 'Interlayer space composition', 'Bandgap, eV', 'Materials Project ID', 'COD_ID', 'Springer_ID', 'Z', 'a, A', 'b, A', 'c, A', 'Symmetry group', 'd,A', 'Number of octahedrons on a layer', 'Prep Method', 'CalcT(K)', 'Calc time (h)', 'Nitrogen', 'Promotion method', 'Promoter', 'Promoter, w%', 'Surface area, m2/g', 'CatW, g/L', 'Alcohol, %', 'Sac Agent 1', 'Sac agent 2', 'Light type', 'Power, W', 'Wave length min, nm', 'Cell material', 'Temperature, K', 'Rate, umol/(g*h)', 'MP_CIF_modifier', 'COD_CIF_modifier', 'Springer_CIF_modifier', 'Materials Project verification', 'COD verification', 'Springer verification', 'General verification', 'MP_CIF_modified', 'COD_CIF_modified', 'Springer_CIF_modified']


In [206]:
df = df[init_columns]
df.info()

<class 'pandas.core.frame.DataFrame'>
RangeIndex: 1089 entries, 0 to 1088
Data columns (total 41 columns):
 #   Column                            Non-Null Count  Dtype  
---  ------                            --------------  -----  
 0   Perovskite                        1089 non-null   object 
 1   Interlayer space composition      5 non-null      object 
 2   Bandgap, eV                       1054 non-null   float64
 3   Materials Project ID              1058 non-null   object 
 4   COD_ID                            935 non-null    object 
 5   Springer_ID                       257 non-null    object 
 6   Z                                 694 non-null    float64
 7   a, A                              735 non-null    object 
 8   b, A                              717 non-null    object 
 9   c, A                              717 non-null    object 
 10  Symmetry group                    494 non-null    object 
 11  d,A                               810 non-null    float64
 12  Number

#Formatting


In [207]:
subs_map = {
    "Ph": "C6H5",
    "Bn": "C7H7",
    #"Pr": "C3H7",
    "Bu": "C4H9",
    "Hx": "C6H13",
    "Me": "CH3",
    "Et": "C2H5",
    "Oc": "C8H17",
    "Dc": "C10H21",
}

import re

def expand_substituents(formula):
    if pd.isna(formula):
        return formula

    for abbr, full in subs_map.items():
        formula = re.sub(rf'{abbr}', full, formula)
    return formula

In [208]:
print(df.shape[0])
df = df[~df['Perovskite'].str.contains("Nx", na=False)]
df = df[~df['Perovskite'].str.contains("Ox", na=False)]
print(df.shape[0])

1089
1076


In [209]:
df['Perovskite'] = df['Perovskite'].apply(expand_substituents)
#print(expand_substituents('HNdTiO4*MeNH2'))

In [210]:
df = df.replace("-", np.nan)
df["a, A"] = df["a, A"].astype("float64")
df["b, A"] = df["b, A"].astype("float64")
df["c, A"] = df["c, A"].astype("float64")
df["Number of octahedrons on a layer"] = df["Number of octahedrons on a layer"].astype("float64")

/tmp/ipython-input-3678714408.py:1: FutureWarning:

Downcasting behavior in `replace` is deprecated and will be removed in a future version. To retain the old behavior, explicitly call `result.infer_objects(copy=False)`. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`



In [211]:
df["Nitrogen"] = df["Nitrogen"].fillna(False)
df["Nitrogen"]
df["Nitrogen"].astype("bool")
df["Nitrogen"].value_counts()

/tmp/ipython-input-1068474039.py:1: FutureWarning:

Downcasting object dtype arrays on .fillna, .ffill, .bfill is deprecated and will change in a future version. Call result.infer_objects(copy=False) instead. To opt-in to the future behavior, set `pd.set_option('future.no_silent_downcasting', True)`



Nitrogen
False    1029
True       47
Name: count, dtype: int64

In [212]:
df["Promoter, w%"] = df["Promoter, w%"].fillna(0)
df["Promoter, w%"].value_counts()

Promoter, w%
0.000     493
1.000     295
0.100      81
0.500      72
0.150      27
0.200      24
0.300      16
3.000      15
2.000      10
4.000       7
5.000       4
0.375       4
0.250       3
1.120       2
7.000       2
0.600       2
0.750       2
0.700       1
0.800       1
0.400       1
1.040       1
1.200       1
1.190       1
1.295       1
1.610       1
1.340       1
0.050       1
0.740       1
0.070       1
0.910       1
0.450       1
0.220       1
1.500       1
10.000      1
Name: count, dtype: int64

In [213]:
df["Surface area, m2/g"] = df["Surface area, m2/g"].astype("float64")
df["Surface area, m2/g"].value_counts()

#df['Materials Project ID'] = df['Materials Project ID'].astype(str)
print(df['Materials Project ID'].dtype)

object


In [214]:
df["Perovskite"].value_counts()

Perovskite
HCa2Nb3O10                   33
La2Ti2O7                     32
H2Nd2Ti3O10*2C4H9NH2         32
TiO2                         30
K4Nb6O17                     28
                             ..
Na2La2Mn0.9Ti2.1O10           1
Na2La2MnTi2O10                1
H0.4K1.6La2Ti3O10*1.07H2O     1
RbNdNb2O7                     1
CsNdNb2O7                     1
Name: count, Length: 450, dtype: int64

In [215]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 1076 entries, 0 to 1088
Data columns (total 41 columns):
 #   Column                            Non-Null Count  Dtype  
---  ------                            --------------  -----  
 0   Perovskite                        1076 non-null   object 
 1   Interlayer space composition      5 non-null      object 
 2   Bandgap, eV                       1041 non-null   float64
 3   Materials Project ID              1045 non-null   object 
 4   COD_ID                            922 non-null    object 
 5   Springer_ID                       257 non-null    object 
 6   Z                                 694 non-null    float64
 7   a, A                              731 non-null    float64
 8   b, A                              713 non-null    float64
 9   c, A                              713 non-null    float64
 10  Symmetry group                    494 non-null    object 
 11  d,A                               799 non-null    float64
 12  Number of o

In [216]:
df.to_excel("checkpoint_formatting.xlsx")


#Data cleaning

##Missing data handling

In [217]:
df.isna().sum()

Perovskite                             0
Interlayer space composition        1071
Bandgap, eV                           35
Materials Project ID                  31
COD_ID                               154
Springer_ID                          819
Z                                    382
a, A                                 345
b, A                                 363
c, A                                 363
Symmetry group                       582
d,A                                  277
Number of octahedrons on a layer     962
Prep Method                           58
CalcT(K)                              79
Calc time (h)                        116
Nitrogen                               0
Promotion method                     488
Promoter                             482
Promoter, w%                           0
Surface area, m2/g                   526
CatW, g/L                            102
Alcohol, %                           123
Sac Agent 1                          989
Sac agent 2                         1050
Light type                            91
Power, W                              95
Wave length min, nm                  399
Cell material                        239
Temperature, K                       548
Rate, umol/(g*h)                     100
MP_CIF_modifier                      566
COD_CIF_modifier                     879
Springer_CIF_modifier                955
Materials Project verification         0
COD verification                       0
Springer verification                  0
General verification                   0
MP_CIF_modified                       31
COD_CIF_modified                     154
Springer_CIF_modified                819
dtype: int64

In [218]:
df.columns

Index(['Perovskite', 'Interlayer space composition', 'Bandgap, eV',
       'Materials Project ID', 'COD_ID', 'Springer_ID', 'Z', 'a, A', 'b, A',
       'c, A', 'Symmetry group', 'd,A', 'Number of octahedrons on a layer',
       'Prep Method', 'CalcT(K)', 'Calc time (h)', 'Nitrogen',
       'Promotion method', 'Promoter', 'Promoter, w%', 'Surface area, m2/g',
       'CatW, g/L', 'Alcohol, %', 'Sac Agent 1', 'Sac agent 2', 'Light type',
       'Power, W', 'Wave length min, nm', 'Cell material', 'Temperature, K',
       'Rate, umol/(g*h)', 'MP_CIF_modifier', 'COD_CIF_modifier',
       'Springer_CIF_modifier', 'Materials Project verification',
       'COD verification', 'Springer verification', 'General verification',
       'MP_CIF_modified', 'COD_CIF_modified', 'Springer_CIF_modified'],
      dtype='object')

In [219]:
drop_columns = ['Perovskite', 'Bandgap, eV',
       'Prep Method', 'CalcT(K)', 'Calc time (h)',
       'CatW, g/L', 'Light type',
       'Power, W',
       'Rate, umol/(g*h)']

drop_columns=['Perovskite','Rate, umol/(g*h)'] #drop nan in these columns

df['Bandgap, eV'] = df['Bandgap, eV'].fillna(df['Bandgap, eV'].mean())
df['Prep Method'] = df['Prep Method'].fillna(df['Prep Method'].mode()[0])
df['CalcT(K)'] = df['CalcT(K)'].fillna(df['CalcT(K)'].mean())
df['Calc time (h)'] = df['Calc time (h)'].fillna(df['Calc time (h)'].mean())
df['CatW, g/L'] = df['CatW, g/L'].fillna(df['CatW, g/L'].mean())
df['Light type'] = df['Light type'].fillna(df['Light type'].mode()[0])
df['Power, W'] = df['Power, W'].fillna(df['Power, W'].mean())

df.dropna(subset=drop_columns, inplace=True)
df.shape[0]

976

In [220]:
df = df[df["General verification"] == False]
df.shape[0]

897

In [221]:
df.isna().sum()

Perovskite                            0
Interlayer space composition        893
Bandgap, eV                           0
Materials Project ID                 18
COD_ID                              121
Springer_ID                         675
Z                                   350
a, A                                318
b, A                                333
c, A                                333
Symmetry group                      493
d,A                                 239
Number of octahedrons on a layer    789
Prep Method                           0
CalcT(K)                              0
Calc time (h)                         0
Nitrogen                              0
Promotion method                    356
Promoter                            352
Promoter, w%                          0
Surface area, m2/g                  401
CatW, g/L                             0
Alcohol, %                           28
Sac Agent 1                         814
Sac agent 2                         872
Light type                            0
Power, W                              0
Wave length min, nm                 282
Cell material                       133
Temperature, K                      429
Rate, umol/(g*h)                      0
MP_CIF_modifier                     466
COD_CIF_modifier                    721
Springer_CIF_modifier               795
Materials Project verification        0
COD verification                      0
Springer verification                 0
General verification                  0
MP_CIF_modified                      18
COD_CIF_modified                    121
Springer_CIF_modified               675
dtype: int64

In [222]:
def calculate_average_specific_area(dataframe):
  total=0;
  n=0;
  for index, row in df.iterrows():
    area =  row['Surface area, m2/g']
    if(np.isnan(area) or area > 55):
      continue
    total += area
    n+=1
  return total/n

In [223]:
avr_specific_area = calculate_average_specific_area(df)
print(avr_specific_area)
df["Surface area, m2/g"] = df["Surface area, m2/g"].fillna(avr_specific_area)

df["Alcohol, %"] = df["Alcohol, %"].fillna(0)
df["Wave length min, nm"] = df["Wave length min, nm"].fillna(df["Wave length min, nm"].min())
df["Cell material"] = df["Cell material"].fillna(df["Cell material"].mode()[0])
print(df["Cell material"].mode()[0])
df["Temperature, K"] = df["Temperature, K"].fillna(298.15)
df["Materials Project ID"] = df["Materials Project ID"].fillna(-1)
df["COD_ID"] = df["COD_ID"].fillna(-1)
df["Springer_ID"] = df["Springer_ID"].fillna(-1)

10.374370192307678
quartz


In [224]:
df["Promoter"] = df["Promoter"].fillna("No promoter")
df["Promotion method"] = df["Promotion method"].fillna("No promotion")

In [225]:
if(finite_log_of_zero_rate):
  df['Rate, umol/(g*h)'].replace(0, 0.1, inplace=True)

df['Log_rate'] = np.log(df['Rate, umol/(g*h)'])
df['Log_rate'].replace([np.inf, -np.inf], np.nan, inplace=True)
df = df.dropna(subset=["Log_rate"])
df['Log_rate'].value_counts()

/usr/local/lib/python3.12/dist-packages/pandas/core/arraylike.py:399: RuntimeWarning:

divide by zero encountered in log

/tmp/ipython-input-952295878.py:5: FutureWarning:

A value is trying to be set on a copy of a DataFrame or Series through chained assignment using an inplace method.
The behavior will change in pandas 3.0. This inplace method will never work because the intermediate object on which we are setting values always behaves as a copy.

For example, when doing 'df[col].method(value, inplace=True)', try using 'df.method({col: value}, inplace=True)' or df[col] = df[col].method(value) instead, to perform the operation inplace on the original object.





Log_rate
2.302585     13
2.995732     10
1.609438     10
1.791759      8
5.298317      7
             ..
3.593569      1
5.176150      1
1.193922      1
4.189655      1
10.668955     1
Name: count, Length: 564, dtype: int64

In [226]:
#raise SystemExit("Stopping execution")
print(df.shape[0])
df = df[df["Sac Agent 1"].isna()]
df = df[df["Sac agent 2"].isna()]
print(df.shape[0])

811
735


In [227]:
df["d,A"] = df["d,A"].fillna(df["d,A"].mean())
print(df["d,A"].mean())


14.096649073197813


In [228]:
df.isna().sum()

Perovskite                            0
Interlayer space composition        731
Bandgap, eV                           0
Materials Project ID                  0
COD_ID                                0
Springer_ID                           0
Z                                   266
a, A                                251
b, A                                252
c, A                                252
Symmetry group                      401
d,A                                   0
Number of octahedrons on a layer    637
Prep Method                           0
CalcT(K)                              0
Calc time (h)                         0
Nitrogen                              0
Promotion method                      0
Promoter                              0
Promoter, w%                          0
Surface area, m2/g                    0
CatW, g/L                             0
Alcohol, %                            0
Sac Agent 1                         735
Sac agent 2                         735
Light type                            0
Power, W                              0
Wave length min, nm                   0
Cell material                         0
Temperature, K                        0
Rate, umol/(g*h)                      0
MP_CIF_modifier                     360
COD_CIF_modifier                    596
Springer_CIF_modifier               665
Materials Project verification        0
COD verification                      0
Springer verification                 0
General verification                  0
MP_CIF_modified                      14
COD_CIF_modified                    111
Springer_CIF_modified               574
Log_rate                              0
dtype: int64

## Duplicates handling

In [229]:
duplicates = df[ df.duplicated()]
duplicates

Empty DataFrame
Columns: [Perovskite, Interlayer space composition, Bandgap, eV, Materials Project ID, COD_ID, Springer_ID, Z, a, A, b, A, c, A, Symmetry group, d,A, Number of octahedrons on a layer, Prep Method, CalcT(K), Calc time (h), Nitrogen, Promotion method, Promoter, Promoter, w%, Surface area, m2/g, CatW, g/L, Alcohol, %, Sac Agent 1, Sac agent 2, Light type, Power, W, Wave length min, nm, Cell material, Temperature, K, Rate, umol/(g*h), MP_CIF_modifier, COD_CIF_modifier, Springer_CIF_modifier, Materials Project verification, COD verification, Springer verification, General verification, MP_CIF_modified, COD_CIF_modified, Springer_CIF_modified, Log_rate]
Index: []

[0 rows x 42 columns]

##Handling outliers

In [230]:
columns_outliers_detedection = [ 'Bandgap, eV',
      'Calc time (h)', 'Promoter, w%', 'Surface area, m2/g',
       'CatW, g/L', 'Alcohol, %',
       'Power, W', 'Wave length min, nm', 'Temperature, K']

columns_outliers_detedection = [ 'Bandgap, eV',
       'Promoter, w%', 'Surface area, m2/g',
       'CatW, g/L', 'Alcohol, %',
       'Power, W', 'Wave length min, nm']
#columns_outliers_detedection=[]

In [231]:
import plotly.express as px
def plot_destribution(df,column):
  #fig = px.histogram(df, x=column,nbins=40,width=800, height=600, title=column)
  fig = px.violin(df, x=column,width=600, height=600, title=column)
  fig.update_layout(font_size=20)
  fig.show()
def plot_histogram(df,column):
  fig = px.histogram(df, x=column,nbins=20,width=600, height=600, title=column)
  fig.update_layout(font_size=20)
  fig.show()

In [232]:
for column in columns_outliers_detedection:
  plot_histogram(df,column)

In [233]:
min_boundries = {
    'Bandgap, eV':2,
    'Calc time (h)':-1,
    'Promoter, w%':-1,
    'Surface area, m2/g':-1,
    'CatW, g/L':-1,
    'Alcohol, %':-1,
    'Power, W':-1,
    'Wave length min, nm':-1,
    'Temperature, K':-1,
}
max_boundries = {
   'Bandgap, eV':4.5,
    'Calc time (h)':100,
    'Promoter, w%':6,
    'Surface area, m2/g':120,
    'CatW, g/L':6,
    'Alcohol, %':40,
    'Power, W':600,
    'Wave length min, nm':450,
    'Temperature, K':320,
}

In [234]:
def manual_column_outliers_removal(_df, _column):
  num_rows_before = _df.shape[0]

  lower_bound = min_boundries.get(_column)
  upper_bound = max_boundries.get(_column)

  if(lower_bound is None):
    return _df

  df_clean = _df[(_df[_column]>= lower_bound) & (_df[_column] <= upper_bound)]
  num_rows_after = df_clean.shape[0]
  removed = num_rows_before - num_rows_after
  print(f'Column: {_column} removed ouliers: {removed }')
  print(f'min: {lower_bound} max: {upper_bound}')
  return df_clean

In [235]:
def IQR_column_outliers_removal(_df, _column):
  num_rows_before = _df.shape[0]
  Q1 = _df[_column].quantile(0.25)
  Q3 = _df[_column].quantile(0.75)
  IQR = Q3 - Q1

  lower_bound = Q1 - 1.5 * IQR
  upper_bound = Q3 + 1.5 * IQR

  df_clean = _df[(_df[_column]>= lower_bound) & (_df[_column] <= upper_bound)]
  num_rows_after = df_clean.shape[0]
  removed = num_rows_before - num_rows_after
  print(f'Column: {_column} removed ouliers: {removed }')
  print(f'min: {lower_bound} max: {upper_bound}')
  return df_clean

In [236]:
if not remove_outliers_after_descriptors and remove_outliers:
  for column in columns_outliers_detedection:
    if(remove_outliers_manually):
      df = manual_column_outliers_removal(df,column)
    else:
      df = IQR_column_outliers_removal(df,column)
print(f'Rows left: {df.shape[0]}')

Column: Bandgap, eV removed ouliers: 29
min: 2 max: 4.5
Column: Promoter, w% removed ouliers: 3
min: -1 max: 6
Column: Surface area, m2/g removed ouliers: 3
min: -1 max: 120
Column: CatW, g/L removed ouliers: 3
min: -1 max: 6
Column: Alcohol, % removed ouliers: 2
min: -1 max: 40
Column: Power, W removed ouliers: 30
min: -1 max: 600
Column: Wave length min, nm removed ouliers: 2
min: -1 max: 450
Rows left: 663


#Featurizing





## Material Project IDs


In [237]:
from mp_api.client import MPRester

API_KEY = "GFsoU5OV3dEngGT860TOtWcn35bE4y6l"
with MPRester(API_KEY) as mpr:
    materials = mpr.materials.search(formula="KCa2Nb3O10")
for material in materials:
    print(material.material_id, material.formula_pretty)

Retrieving MaterialsDoc documents:   0%|          | 0/2 [00:00<?, ?it/s]

mp-557195 KCa2Nb3O10
mp-1223594 KCa2Nb3O10


In [238]:
def get_material_id_by_formula(f):
  with MPRester(API_KEY) as mpr:
    print(f"Composition: {f}")
    try:
      materials = mpr.materials.search(formula=f)
      if len(materials)>0:
        print(f"Composition: {f} ID is {materials[0].material_id}")
        return str(materials[0].material_id)
      else:
        print(f"Composition: {f} ID is not found")
        return str(-1)
    except Exception as e:
      print(f"Composition: {f} ID is not found")
      return str(-1)

In [239]:
def update_Materials_Project_IDs(_df):
  for index, row in _df.iterrows():
        if pd.isna(row['Materials Project ID']) or row['Materials Project ID']==-1 or row['Materials Project ID']==-2 :
            new_id = get_material_id_by_formula(row['Perovskite'])
            print(f"New ID fetched: {new_id}  for formula {row['Perovskite']}")
            _df.at[index, 'Materials Project ID'] = str(new_id)
  return _df

In [240]:
if update_IDs:
  df = update_Materials_Project_IDs(df)

##HIll's formula

In [241]:
import re
from collections import Counter
def parse_formula(formula):
    """Extracts element counts from a chemical formula."""
    pattern = r"([A-Z][a-z]*)(\d*)"
    matches = re.findall(pattern, formula)

    element_counts = Counter()
    for element, count in matches:
        element_counts[element] += int(count) if count else 1  # Default to 1 if count is missing

    return element_counts
def to_hill_notation(formula):
    """Converts a chemical formula to Hill notation."""
    element_counts = parse_formula(formula)

    # Hill notation rules
    if "C" in element_counts:
        elements_sorted = ["C", "H"] if "H" in element_counts else ["C"]
        remaining_elements = sorted(e for e in element_counts if e not in ["C", "H"])
        elements_sorted.extend(remaining_elements)
    else:
        elements_sorted = sorted(element_counts.keys())
    hill_formula = " ".join(f"{el}{element_counts[el] if element_counts[el] > 1 else ''}" for el in elements_sorted)
    #print(f':{hill_formula}:')
    return hill_formula


In [242]:
formulas = ["H2O", "C6H12O6", "NH3", "Fe2O3", "CH4", "CCl4", "H4C", "KCa2Nb3O10"]
for f in formulas:
    print(f"{f} -> {to_hill_notation(f)}")

H2O -> H2 O
C6H12O6 -> C6 H12 O6
NH3 -> H3 N
Fe2O3 -> Fe2 O3
CH4 -> C H4
CCl4 -> C Cl4
H4C -> C H4
KCa2Nb3O10 -> Ca2 K Nb3 O10


In [243]:
df['Hill formula']=df['Perovskite'].apply(to_hill_notation)
df

Perovskite Interlayer space composition  Bandgap, eV  \
0       K4Nb6O17                          NaN         3.50   
1       KLaNb2O7                          NaN         3.20   
2      RbLaNb2O7                          NaN         3.35   
3      CsLaNb2O7                          NaN         3.30   
4     KCa2Nb3O10                          NaN         3.35   
...          ...                          ...          ...   
1084        TiO2                          NaN         3.20   
1085        TiO2                          NaN         3.20   
1086        TiO2                          NaN         3.20   
1087        TiO2                          NaN         3.20   
1088        TiO2                          NaN         3.20   

     Materials Project ID   COD_ID Springer_ID    Z   a, A   b, A    c, A  \
0               mp-560692  1001842          -1  4.0  6.600  7.940  33.700   
1              mp-1223501  1545643          -1  8.0  7.806  7.668  21.540   
2               mp-553965       -1          -1  1.0  3.885  3.885  10.989   
3               mp-553248  2004917          -1  1.0  3.905  3.905  11.185   
4               mp-557195  1521061          -1  8.0  7.727  7.727  29.466   
...                   ...      ...         ...  ...    ...    ...     ...   
1084           mp-1245098  1010942          -1  NaN    NaN    NaN     NaN   
1085           mp-1245098  1010942          -1  NaN    NaN    NaN     NaN   
1086           mp-1245098  1010942          -1  NaN    NaN    NaN     NaN   
1087           mp-1245098  1010942          -1  NaN    NaN    NaN     NaN   
1088           mp-1245098  1010942          -1  NaN    NaN    NaN     NaN   

      ... Springer_CIF_modifier  Materials Project verification  \
0     ...                   NaN                            True   
1     ...                   NaN                            True   
2     ...                   NaN                            True   
3     ...                   NaN                            True   
4     ...                   NaN                            True   
...   ...                   ...                             ...   
1084  ...                   NaN                            True   
1085  ...                   NaN                            True   
1086  ...                   NaN                            True   
1087  ...                   NaN                            True   
1088  ...                   NaN                            True   

      COD verification Springer verification  General verification  \
0                 True                 False                 False   
1                 True                 False                 False   
2                False                 False                 False   
3                 True                 False                 False   
4                 True                 False                 False   
...                ...                   ...                   ...   
1084              True                 False                 False   
1085              True                 False                 False   
1086              True                 False                 False   
1087              True                 False                 False   
1088              True                 False                 False   

      MP_CIF_modified  COD_CIF_modified Springer_CIF_modified  Log_rate  \
0           mp-560692           1001842                   NaN  4.867534   
1          mp-1223501           1545643                   NaN  3.332205   
2           mp-553965                -1                   NaN  4.094345   
3           mp-553248           2004917                   NaN  2.484907   
4           mp-557195           1521061                   NaN  2.639057   
...               ...               ...                   ...       ...   
1084       mp-1245098           1010942                   NaN  3.642359   
1085       mp-1245098           1010942                   NaN  3.593569   
1086       mp-1

##COD_IDs


In [244]:
def get_COD_ID_for_formula(formula):
  print(f"Formula :{formula}:")
  url=f"https://www.crystallography.net/cod/result?formula={formula}&format=json"
  response = requests.get(url)
  if response.status_code == 200:
    data = response.json()
    #print("Len: ",len(data))
    if(len(data)>0):
      #print(data[0]['file'])
      return data[0]['file']
  print(-1)
  return -1

def update_COD_ID(_df):
  for index, row in _df.iterrows():
        if pd.isna(row['COD_ID']) or row['COD_ID']==-1 or row['COD_ID']==-2 :
            print(f"New ID fetching start for formula {row['Hill formula']}")
            new_id = get_COD_ID_for_formula(row['Hill formula'])
            print(f"New ID fetched: {new_id}  for formula {row['Hill formula']}")
            _df.at[index, 'COD_ID'] = new_id
  return _df


In [245]:
df.to_excel('checkpoint_Hill_formula.xlsx')
#print(get_COD_ID("O2 Ti"))
if update_IDs:
  df = update_COD_ID(df)

##CIF files extraction

In [246]:
def extract_CIF_from_MP(material_id):
  if pd.isna(material_id) or material_id == "-1" or material_id == -1 or material_id == -2:
     print("Skipping invalid ID:", material_id)
     return
  print("ID: ", material_id)

  path = f'/content/drive/MyDrive/University/Artificial intelligence in chemistry/Perovskite project/Perovskite-liked-oxides-bandgap-prediction/Data/CIF/{material_id}.cif'
  if os.path.exists(path):
    print(f'CIF file for {material_id} already exist')
    return

  with MPRester(API_KEY) as mpr:
    #data = mpr.materials.search(material_ids=material_id)
    structure = mpr.materials.get_structure_by_material_id(material_id )
    cif_string = structure.to("struct.cif")

  ##with open(f"{material_id}.cif", "w") as f:
  #    f.write(cif_string)
  with open(f'/content/drive/MyDrive/University/Artificial intelligence in chemistry/Perovskite project/Perovskite-liked-oxides-bandgap-prediction/Data/CIF/{material_id}.cif', 'w') as f:
      f.write(cif_string)
  print("ID: ", material_id, " done!")

In [247]:
import os
def extract_cif_from_COD(COD_ID):
  if(COD_ID==-1 or COD_ID==-2 ):
    return
  print(COD_ID)
  path = f'/content/drive/MyDrive/University/Artificial intelligence in chemistry/Perovskite project/Perovskite-liked-oxides-bandgap-prediction/Data/CIF/{COD_ID}.cif'
  if os.path.exists(path):
    print(f'CIF file for {COD_ID} already exist')
    return

  url = f"https://www.crystallography.net/cod/{COD_ID}.cif"
  response = requests.get(url)

  ##with open(f"{material_id}.cif", "w") as f:
  #    f.write(cif_string)
  if response.status_code == 200:
    print("Sucess")
    with open(path, 'w') as f:
        f.write(response.text)
  else:
    print('No CIF')

In [248]:
if extract_CIFs:
  for material_id in df['COD_ID'].unique():
    extract_cif_from_COD(material_id)

In [249]:
if extract_CIFs:
  for material_id in df['Materials Project ID'].unique():
    extract_CIF_from_MP(material_id)

##Valence electron discriptors

In [250]:
from matminer.featurizers.composition import ElementProperty
from matminer.featurizers.composition import ValenceOrbital
from pymatgen.core.composition import Composition


In [251]:
df['composition_obj'] = df['Hill formula'].apply(Composition)
print("Null compositions",df['composition_obj'].isna().sum())
vo_feat = ValenceOrbital()
df = vo_feat.featurize_dataframe(df, col_id='composition_obj')
df = df.drop('composition_obj', axis=1)

Null compositions 0


/usr/local/lib/python3.12/dist-packages/matminer/featurizers/composition/orbital.py:115: UserWarning:

ValenceOrbital(impute_nan=False):
In a future release, impute_nan will be set to True by default.
                    This means that features that are missing or are NaNs for elements
                    from the data source will be replaced by the average of that value
                    over the available elements.
                    This avoids NaNs after featurization that are often replaced by
                    dataset-dependent averages.

/usr/local/lib/python3.12/dist-packages/matminer/utils/data.py:326: UserWarning:

MagpieData(impute_nan=False):
In a future release, impute_nan will be set to True by default.
                    This means that features that are missing or are NaNs for elements
                    from the data source will be replaced by the average of that value
                    over the available elements.
                    This avoids NaNs after f

ValenceOrbital:   0%|          | 0/663 [00:00<?, ?it/s]

##Mulliken electronegativity

In [252]:
from pymatgen.core.periodic_table import Element

def get_mulliken_en(element_symbol):
    el = Element(element_symbol)
    IE = el.ionization_energies[0]  # First ionization energy in eV
    EA = el.electron_affinity       # Electron affinity in eV

    if IE is None or EA is None:
        return None

    return (IE + EA) / 2


def calc_average_electronegativity(formula):
  # Example: For Fe2O3
  comp = Composition(formula)
  # Weighted mean electronegativity
  total_atoms = comp.num_atoms
  mean_en = sum(
    #comp[el] / total_atoms * Element(el).X
    comp[el] / total_atoms * get_mulliken_en(el)
    for el in comp.elements)
  return mean_en

In [253]:
df["Average Mulliken electronegativity"] = df["Hill formula"].apply(calc_average_electronegativity)

##Valence electron density

In [254]:
def split_formula(formula):
  output={}
  elements_with_indexes = formula.split()
  for el in elements_with_indexes:
    #match = re.match(r"([A-Za-z]+)(\d+)$", el)
    match = re.match(r"([A-Za-z]+)(\d+(?:\.\d+)?)$", el)
    if match:
      output[match.group(1)]=float(match.group(2))
    else:
      output[ el]=float(1)
  return output

def get_valence_electrons_number(hill_fomula):
  split = split_formula(hill_fomula)
  print(split)
  v = split.get("O")
  if v == None:
    return 0
  else:
    return 2*v

In [255]:
df["Valence electrons"] = df["Hill formula"].apply(get_valence_electrons_number)

{'K': 4.0, 'Nb': 6.0, 'O': 17.0}
{'K': 1.0, 'La': 1.0, 'Nb': 2.0, 'O': 7.0}
{'La': 1.0, 'Nb': 2.0, 'O': 7.0, 'Rb': 1.0}
{'Cs': 1.0, 'La': 1.0, 'Nb': 2.0, 'O': 7.0}
{'Ca': 2.0, 'K': 1.0, 'Nb': 3.0, 'O': 10.0}
{'Ca': 2.0, 'Nb': 3.0, 'O': 10.0, 'Rb': 1.0}
{'Ca': 2.0, 'Cs': 1.0, 'Nb': 3.0, 'O': 10.0}
{'K': 1.0, 'Nb': 3.0, 'O': 10.0, 'Sr': 2.0}
{'K': 4.0, 'Nb': 6.0, 'O': 17.0}
{'K': 1.0, 'La': 1.0, 'Nb': 2.0, 'O': 7.0}
{'La': 1.0, 'Nb': 2.0, 'O': 7.0, 'Rb': 1.0}
{'Cs': 1.0, 'La': 1.0, 'Nb': 2.0, 'O': 7.0}
{'Ca': 2.0, 'K': 1.0, 'Nb': 3.0, 'O': 10.0}
{'Ca': 2.0, 'Nb': 3.0, 'O': 10.0, 'Rb': 1.0}
{'Ca': 2.0, 'Cs': 1.0, 'Nb': 3.0, 'O': 10.0}
{'K': 1.0, 'Nb': 3.0, 'O': 10.0, 'Sr': 2.0}
{'O': 2.0, 'Ti': 1.0}
{'H': 4.0, 'Nb': 6.0, 'O': 17.0}
{'H': 1.0, 'La': 1.0, 'Nb': 2.0, 'O': 7.0}
{'H': 1.0, 'La': 1.0, 'Nb': 2.0, 'O': 7.0}
{'H': 1.0, 'La': 1.0, 'Nb': 2.0, 'O': 7.0}
{'Ca': 2.0, 'H': 1.0, 'Nb': 3.0, 'O': 10.0}
{'Ca': 2.0, 'H': 1.0, 'Nb': 3.0, 'O': 10.0}
{'Ca': 2.0, 'H': 1.0, 'Nb': 3.0, 'O': 10.0}


##CIF files descriptors

In [256]:
from pymatgen.core.structure import Structure

def getCellVolume(ID):
  print("getCellVolume() ID:",ID)
  if(ID==-1):
    return 0
  file_path=f"/content/drive/MyDrive/University/Artificial intelligence in chemistry/Perovskite project/Perovskite-liked-oxides-bandgap-prediction/Data/CIF/{ID}.cif"
  if os.path.exists(file_path):
    try:
      structure = Structure.from_file(file_path)
    except:
      print('ERROR: Invalid structure for ',ID)
      return 0
  else:
    return 0

  if(structure == None):
    return 0
  return structure.volume

In [257]:
def getCellZValue(ID):
  if(ID==-1):
    return 0
  file_path=f"/content/drive/MyDrive/University/Artificial intelligence in chemistry/Perovskite project/Perovskite-liked-oxides-bandgap-prediction/Data/CIF/{ID}.cif"
  if os.path.exists(file_path):
    try:
      structure = Structure.from_file(file_path)
    except:
      print('ERROR: Invalid structure for ',ID)
      return 0
  else:
    return 0
  if(structure == None):
    return 0
  return structure.composition.num_atoms / structure.composition.reduced_composition.num_atoms

In [258]:
def abcExtractionFromMP(ID):
  if(ID==-1):
    return 0
  file_path=f"/content/drive/MyDrive/University/Artificial intelligence in chemistry/Perovskite project/Perovskite-liked-oxides-bandgap-prediction/Data/CIF/{ID}.cif"
  if os.path.exists(file_path):
    try:
      structure = Structure.from_file(file_path)
    except:
      print('ERROR: Invalid structure for ',ID)
      return [0,0,0]
  else:
    return  [0,0,0]

  if(structure == None):
    return  [0,0,0]
  a = structure.lattice.a
  b = structure.lattice.b
  c = structure.lattice.c
  return [a,b,c]

In [259]:
CIF_source = "MP_CIF_modified"
if(extract_CIFs):
  CIF_source = "Materials Project ID"

df["Volume_MP"]=df[CIF_source].apply(getCellVolume)
df["Z_MP"]=df[CIF_source].apply(getCellZValue)
df['Valence Electrons Density_MP'] = (df['Valence electrons'] * df['Z_MP']) / df['Volume_MP']
df[['a_MP', 'b_MP', 'c_MP']] = df[CIF_source].apply(abcExtractionFromMP).apply(pd.Series)

getCellVolume() ID: mp-560692
getCellVolume() ID: mp-1223501
getCellVolume() ID: mp-553965
getCellVolume() ID: mp-553248
getCellVolume() ID: mp-557195
getCellVolume() ID: mp-20396
getCellVolume() ID: mp-581330
getCellVolume() ID: M_MP0
getCellVolume() ID: mp-560692
getCellVolume() ID: mp-1223501
getCellVolume() ID: mp-553965
getCellVolume() ID: mp-553248
getCellVolume() ID: mp-557195
getCellVolume() ID: mp-20396
getCellVolume() ID: mp-581330
getCellVolume() ID: M_MP1
getCellVolume() ID: mp-1245098
getCellVolume() ID: M_MP2
getCellVolume() ID: mp-1205881
getCellVolume() ID: mp-1205881
getCellVolume() ID: mp-1205881
getCellVolume() ID: M_MP3
getCellVolume() ID: M_MP4
getCellVolume() ID: M_MP5
getCellVolume() ID: M_MP6
getCellVolume() ID: M_MP7
getCellVolume() ID: mp-1205881
getCellVolume() ID: mp-1205881
getCellVolume() ID: mp-1205881
getCellVolume() ID: M_MP8
getCellVolume() ID: M_MP9
getCellVolume() ID: M_MP10
getCellVolume() ID: M_MP11
getCellVolume() ID: mp-560692
getCellVolume() ID:

/usr/local/lib/python3.12/dist-packages/pymatgen/core/structure.py:3109: UserWarning:

Issues encountered while parsing CIF: 24 fractional coordinates rounded to ideal values to avoid issues with finite precision.

/usr/local/lib/python3.12/dist-packages/pymatgen/core/structure.py:3109: UserWarning:

Issues encountered while parsing CIF: 12 fractional coordinates rounded to ideal values to avoid issues with finite precision.



getCellVolume() ID: M_MP16
getCellVolume() ID: M_MP17
getCellVolume() ID: M_MP18
getCellVolume() ID: M_MP19
getCellVolume() ID: M_MP20
getCellVolume() ID: M_MP21
getCellVolume() ID: M_MP22
getCellVolume() ID: M_MP23
getCellVolume() ID: M_MP24
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: mp-3614
getCellVolume() ID: mp-10347
getCellVolume() ID: M_MP25
getCellVolume() ID: M_MP26
getCellVolume() ID: mp-10347
getCellVolume() ID: M_MP27
getCellVolume() ID: M_MP28
getCellVolume() ID: mp-1104930
getCellVolume() ID: M_MP31
getCellVolume() ID: M_MP32
getCellVolume() ID: M_MP33
getCellVolume() ID: M_MP34
getCellVolume() ID: M_MP35
getCellVolume() ID: mp-1104930
getCellVolume() ID: M_MP36
getCellVolume() ID: M_MP37
getCellVolume() ID: M_MP38
getCellVolume() ID: M_MP39
getCellVolume() ID: M_MP40
getCellVolume() ID: M_MP49
getCellVolume() ID: M_MP50
getCellVolume() ID: M_MP53
getCellVolume() ID: M_MP54
getCellVolume() ID: mp-9904

/usr/local/lib/python3.12/dist-packages/pymatgen/io/cif.py:1314: UserWarning:

Missing elements K from PMG structure composition



getCellVolume() ID: M_MP225
getCellVolume() ID: M_MP226
getCellVolume() ID: M_MP227
getCellVolume() ID: M_MP228
getCellVolume() ID: M_MP229
getCellVolume() ID: M_MP230
getCellVolume() ID: M_MP231
getCellVolume() ID: M_MP232
getCellVolume() ID: M_MP233
getCellVolume() ID: M_MP235
getCellVolume() ID: HLaTiO4_MeNH2
getCellVolume() ID: HLaTiO4_EtNH2
getCellVolume() ID: HLaTiO4_PrNH2
getCellVolume() ID: HLaTiO4_BuNH2
getCellVolume() ID: HLaTiO4_HxNH2
getCellVolume() ID: HLaTiO4_MeOH
getCellVolume() ID: HLaTiO4_EtOH
getCellVolume() ID: HLaTiO4_PrOH
getCellVolume() ID: HLaTiO4_BuOH
getCellVolume() ID: HLaTiO4_HxOH
getCellVolume() ID: M_MP236
getCellVolume() ID: M_MP237
getCellVolume() ID: M_MP238
getCellVolume() ID: M_MP239
getCellVolume() ID: M_MP240
getCellVolume() ID: M_MP241
getCellVolume() ID: M_MP242
getCellVolume() ID: M_MP243
getCellVolume() ID: M_MP244
getCellVolume() ID: M_MP245
getCellVolume() ID: M_MP246
getCellVolume() ID: M_MP248
getCellVolume() ID: M_MP249
getCellVolume() ID: M

/usr/local/lib/python3.12/dist-packages/pymatgen/core/structure.py:3109: UserWarning:

Issues encountered while parsing CIF: 24 fractional coordinates rounded to ideal values to avoid issues with finite precision.

/usr/local/lib/python3.12/dist-packages/pymatgen/core/structure.py:3109: UserWarning:

Issues encountered while parsing CIF: 12 fractional coordinates rounded to ideal values to avoid issues with finite precision.

/usr/local/lib/python3.12/dist-packages/pymatgen/io/cif.py:1314: UserWarning:

Missing elements K from PMG structure composition

/usr/local/lib/python3.12/dist-packages/pymatgen/core/structure.py:3109: UserWarning:

Issues encountered while parsing CIF: 24 fractional coordinates rounded to ideal values to avoid issues with finite precision.

/usr/local/lib/python3.12/dist-packages/pymatgen/core/structure.py:3109: UserWarning:

Issues encountered while parsing CIF: 12 fractional coordinates rounded to ideal values to avoid issues with finite precision.

/usr/local

In [260]:
CIF_source = "COD_CIF_modified"
if(extract_CIFs):
  CIF_source = "COD_ID"

df["Volume_COD"]=df[CIF_source].apply(getCellVolume)
df["Z_COD"]=df[CIF_source].apply(getCellZValue)
df['Valence Electrons Density_COD'] = (df['Valence electrons'] * df['Z_COD']) / df['Volume_COD']
df[['a_COD', 'b_COD', 'c_COD']] = df[CIF_source].apply(abcExtractionFromMP).apply(pd.Series)

getCellVolume() ID: 1001842
getCellVolume() ID: 1545643
getCellVolume() ID: -1
getCellVolume() ID: 2004917
getCellVolume() ID: 1521061
getCellVolume() ID: 2238958
getCellVolume() ID: 1518045


/usr/local/lib/python3.12/dist-packages/pymatgen/io/cif.py:1314: UserWarning:

Incorrect stoichiometry:
  CIF={'K': 1.0, 'La': 1.0, 'Nb': 2.0, 'O': 7.0}
  PMG={'K': 2.188, 'La': 1.936, 'Nb': 4.0, 'O': 14.0}
  ratios={'La': 1.936, 'Nb': 2.0, 'K': 2.188, 'O': 2.0}



getCellVolume() ID: -1
getCellVolume() ID: 1001842
getCellVolume() ID: 1545643
getCellVolume() ID: -1
getCellVolume() ID: 2004917
getCellVolume() ID: 1521061
getCellVolume() ID: 2238958
getCellVolume() ID: 1518045
getCellVolume() ID: -1
getCellVolume() ID: 1010942
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: M_COD0
getCellVolume() ID: M_COD1
getCellVolume() ID: M_COD2
getCellVolume() ID: M_COD3
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: M_COD4
getCellVolume() ID: M_COD5
getCellVolume() ID: M_COD6
getCellVolume() ID: M_COD7
getCellVolume() ID: 1001842
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: 1001842
getCellVolume() ID: 1001842
getCellVolume() ID: 1001842
getCellVolume() ID: 1001842
getCellVolume() ID: 1001842
getCellVolume() ID: -1
getCellVolume() ID: -1
getCellVolume() ID: -1
getCellVolume() ID: -1
getCellVolume() ID:

/usr/local/lib/python3.12/dist-packages/pymatgen/core/structure.py:3109: UserWarning:

Issues encountered while parsing CIF: 8 fractional coordinates rounded to ideal values to avoid issues with finite precision.

/usr/local/lib/python3.12/dist-packages/pymatgen/core/structure.py:3109: UserWarning:

Issues encountered while parsing CIF: 3 fractional coordinates rounded to ideal values to avoid issues with finite precision.

/usr/local/lib/python3.12/dist-packages/pymatgen/core/structure.py:3109: UserWarning:

Issues encountered while parsing CIF: 6 fractional coordinates rounded to ideal values to avoid issues with finite precision.



getCellVolume() ID: 1526720
getCellVolume() ID: -1
getCellVolume() ID: -1
getCellVolume() ID: 1526777
getCellVolume() ID: 2002850
getCellVolume() ID: 2002850
getCellVolume() ID: 1001842
getCellVolume() ID: M_COD12
getCellVolume() ID: M_COD13
getCellVolume() ID: M_COD14
getCellVolume() ID: M_COD15
getCellVolume() ID: M_COD16
getCellVolume() ID: M_COD17
getCellVolume() ID: M_COD18
getCellVolume() ID: M_COD19
getCellVolume() ID: M_COD20
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: 2102087
getCellVolume() ID: 1522043
getCellVolume() ID: 7221084
getCellVolume() ID: nan
getCellVolume() ID: 1522043
getCellVolume() ID: 7221084
getCellVolume() ID: -1
getCellVolume() ID: 2229871
getCellVolume() ID: 2229871
getCellVolume() ID: 2229871
getCellVolume() ID: 2229871
getCellVolume() ID: 2229871
getCellVolume() ID: M_COD21
getCellVolume() ID: 2229871
getCellVolume() ID: 2229871
getCellVolume() ID: 2229871
getCellVolume() ID: 2229871

/usr/local/lib/python3.12/dist-packages/pymatgen/io/cif.py:1314: UserWarning:

Incorrect stoichiometry:
  CIF={'Ba': 1.0, 'Bi': 4.0, 'O': 15.0, 'Ti': 4.0}
  PMG={'Ti': 16.0, 'Ba': 3.76, 'Bi': 16.239999999999995, 'O': 60.0}
  ratios={'Ba': 3.76, 'Ti': 4.0, 'O': 4.0, 'Bi': 4.059999999999999}



getCellVolume() ID: -1
getCellVolume() ID: 1522041
getCellVolume() ID: M_COD23
getCellVolume() ID: 1522039
getCellVolume() ID: M_COD24
getCellVolume() ID: 1522043
getCellVolume() ID: 1522041
getCellVolume() ID: M_COD25
getCellVolume() ID: M_COD26
getCellVolume() ID: -1
getCellVolume() ID: M_COD32
getCellVolume() ID: M_COD33
getCellVolume() ID: M_COD34
getCellVolume() ID: M_COD35
getCellVolume() ID: M_COD36
getCellVolume() ID: M_COD37
getCellVolume() ID: M_COD38
getCellVolume() ID: M_COD39
getCellVolume() ID: M_COD40
getCellVolume() ID: M_COD41
getCellVolume() ID: 1010942
getCellVolume() ID: 1010942
getCellVolume() ID: 1522039
getCellVolume() ID: 1522039
getCellVolume() ID: 1522039
getCellVolume() ID: 1522039
getCellVolume() ID: 7039788
getCellVolume() ID: 7039788
getCellVolume() ID: 7039788
getCellVolume() ID: 1011128
getCellVolume() ID: 2002850
getCellVolume() ID: 1001022
getCellVolume() ID: -1
getCellVolume() ID: 1010942
getCellVolume() ID: 1001842
getCellVolume() ID: M_COD48
getCell

/usr/local/lib/python3.12/dist-packages/pymatgen/io/cif.py:1314: UserWarning:

Incorrect stoichiometry:
  CIF={'K': 1.0, 'La': 1.0, 'Nb': 2.0, 'O': 7.0}
  PMG={'K': 2.188, 'La': 1.936, 'Nb': 4.0, 'O': 14.0}
  ratios={'La': 1.936, 'Nb': 2.0, 'K': 2.188, 'O': 2.0}

/usr/local/lib/python3.12/dist-packages/pymatgen/core/structure.py:3109: UserWarning:

Issues encountered while parsing CIF: 8 fractional coordinates rounded to ideal values to avoid issues with finite precision.

/usr/local/lib/python3.12/dist-packages/pymatgen/core/structure.py:3109: UserWarning:

Issues encountered while parsing CIF: 3 fractional coordinates rounded to ideal values to avoid issues with finite precision.

/usr/local/lib/python3.12/dist-packages/pymatgen/core/structure.py:3109: UserWarning:

Issues encountered while parsing CIF: 6 fractional coordinates rounded to ideal values to avoid issues with finite precision.

/usr/local/lib/python3.12/dist-packages/pymatgen/io/cif.py:1314: UserWarning:

Incorrect stoic

In [261]:
CIF_source = "Springer_CIF_modified"
if(extract_CIFs):
  CIF_source = "Springer_ID"

df["Volume_Springer"]=df[CIF_source].apply(getCellVolume)
df["Z_Springer"]=df[CIF_source].apply(getCellZValue)
df['Valence Electrons Density_Springer'] = (df['Valence electrons'] * df['Z_Springer']) / df['Volume_Springer']
df[['a_Springer', 'b_Springer', 'c_Springer']] = df[CIF_source].apply(abcExtractionFromMP).apply(pd.Series)

getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: sd_1614775
ERROR: Invalid structure for  sd_1614775
getCellVolume() ID: sd_1614775
ERROR: Invalid structure for  sd_1614775
getCellVolume() ID: sd_1614775
ERROR: Invalid structure for  sd_1614775
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() 

/usr/local/lib/python3.12/dist-packages/pymatgen/io/cif.py:286: UserWarning:

Possible issue in CIF file at line: No transformation from published to standardized cell parameters necessary.

/usr/local/lib/python3.12/dist-packages/pymatgen/io/cif.py:286: UserWarning:

Possible issue in CIF file at line: ?

/usr/local/lib/python3.12/dist-packages/pymatgen/io/cif.py:1029: UserWarning:

No _symmetry_equiv_pos_as_xyz type key found. Defaulting to P1.

/usr/local/lib/python3.12/dist-packages/pymatgen/core/structure.py:3109: UserWarning:

No structure parsed for section 1 in CIF.
'_atom_site_label'

/usr/local/lib/python3.12/dist-packages/pymatgen/io/cif.py:1044: UserWarning:

t parsed as T

/usr/local/lib/python3.12/dist-packages/pymatgen/core/structure.py:3109: UserWarning:

No structure parsed for section 3 in CIF.
could not convert string to float: 't'

/usr/local/lib/python3.12/dist-packages/pymatgen/core/structure.py:3109: UserWarning:

No structure parsed for section 4 in CIF.
could n

getCellVolume() ID: M_Springer1
getCellVolume() ID: M_Springer2
getCellVolume() ID: M_Springer3
getCellVolume() ID: sd_1050391
getCellVolume() ID: M_Springer4
getCellVolume() ID: M_Springer5
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: M_Springer6
getCellVolume() ID: sd_1050391
getCellVolume() ID: M_Springer7
getCellVolume() ID: M_Springer8
getCellVolume() ID: sd_1232960
getCellVolume() ID: sd_0314261
getCellVolume() ID: sd_0551678
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: sd_0306542
getCellVolume() ID: sd_0306445
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: sd_0306542
getCellVolume() 

/usr/local/lib/python3.12/dist-packages/pymatgen/core/structure.py:3109: UserWarning:

Issues encountered while parsing CIF: Pauling file corrections applied.
No structure parsed for section 1 in CIF.
'_atom_site_label'
No _symmetry_equiv_pos_as_xyz type key found. Spacegroup from _symmetry_space_group_name_H-M used.
No _symmetry_equiv_pos_as_xyz type key found. Spacegroup from _symmetry_space_group_name_H-M used.
No _symmetry_equiv_pos_as_xyz type key found. Defaulting to P1.

/usr/local/lib/python3.12/dist-packages/pymatgen/core/structure.py:3109: UserWarning:

Issues encountered while parsing CIF: Pauling file corrections applied.
10 fractional coordinates rounded to ideal values to avoid issues with finite precision.
No structure parsed for section 1 in CIF.
'_atom_site_label'
No _symmetry_equiv_pos_as_xyz type key found. Spacegroup from _symmetry_space_group_name_H-M used.
No _symmetry_equiv_pos_as_xyz type key found. Spacegroup from _symmetry_space_group_name_H-M used.
No _symmet

getCellVolume() ID: M_Springer9
getCellVolume() ID: M_Springer10
getCellVolume() ID: M_Springer11
getCellVolume() ID: M_Springer12
getCellVolume() ID: M_Springer13
getCellVolume() ID: M_Springer14
getCellVolume() ID: M_Springer15
getCellVolume() ID: M_Springer16
getCellVolume() ID: M_Springer17
getCellVolume() ID: sd_0314261
getCellVolume() ID: sd_0308503
getCellVolume() ID: sd_1127671
getCellVolume() ID: sd_1232960
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: nan
getCellVolume() ID: M_Springer26
getCellVolume() ID: M_Springer27
getCellVolume() ID: M_Springer30
getCellVolume() ID: M_Spr

...

/usr/local/lib/python3.12/dist-packages/pymatgen/core/structure.py:3109: UserWarning:

Issues encountered while parsing CIF: 4 fractional coordinates rounded to ideal values to avoid issues with finite precision.
No structure parsed for section 1 in CIF.
'_atom_site_label'
No _symmetry_equiv_pos_as_xyz type key found. Spacegroup from _symmetry_space_group_name_H-M used.
No _symmetry_equiv_pos_as_xyz type key found. Spacegroup from _symmetry_space_group_name_H-M used.
No _symmetry_equiv_pos_as_xyz type key found. Defaulting to P1.

/usr/local/lib/python3.12/dist-packages/pymatgen/io/cif.py:286: UserWarning:

Possible issue in CIF file at line: No transformation from published to standardized cell parameters necessary.

/usr/local/lib/python3.12/dist-packages/pymatgen/io/cif.py:286: UserWarning:

Possible issue in CIF file at line: ?

/usr/local/lib/python3.12/dist-packages/pymatgen/io/cif.py:1029: UserWarning:

No _symmetry_equiv_pos_as_xyz type key found. Defaulting to P1.

/usr/local/

ERROR: Invalid structure for  sd_1925412
ERROR: Invalid structure for  sd_1925412
ERROR: Invalid structure for  sd_1925412
ERROR: Invalid structure for  sd_1925412
ERROR: Invalid structure for  sd_1925412
ERROR: Invalid structure for  sd_1925412
ERROR: Invalid structure for  sd_1925412
ERROR: Invalid structure for  sd_1925412
ERROR: Invalid structure for  sd_1925412
ERROR: Invalid structure for  sd_1925412
ERROR: Invalid structure for  sd_1925412


/usr/local/lib/python3.12/dist-packages/pymatgen/core/structure.py:3109: UserWarning:

Issues encountered while parsing CIF: No structure parsed for section 1 in CIF.
'_atom_site_label'
No _symmetry_equiv_pos_as_xyz type key found. Spacegroup from _symmetry_space_group_name_H-M used.
No _symmetry_equiv_pos_as_xyz type key found. Spacegroup from _symmetry_space_group_name_H-M used.
t parsed as T
No structure parsed for section 3 in CIF.
could not convert string to float: 't'
No _symmetry_equiv_pos_as_xyz type key found. Defaulting to P1.
t parsed as T
No structure parsed for section 4 in CIF.
could not convert string to float: 't'

/usr/local/lib/python3.12/dist-packages/pymatgen/core/structure.py:3109: UserWarning:

Issues encountered while parsing CIF: No structure parsed for section 1 in CIF.
'_atom_site_label'
No _symmetry_equiv_pos_as_xyz type key found. Defaulting to P1.
No _symmetry_equiv_pos_as_xyz type key found. Defaulting to P1.
t parsed as T
No structure parsed for section 3

ERROR: Invalid structure for  sd_1210175
ERROR: Invalid structure for  sd_1925412
ERROR: Invalid structure for  sd_1614775
ERROR: Invalid structure for  sd_1925412
ERROR: Invalid structure for  sd_1925412
ERROR: Invalid structure for  sd_1241787
ERROR: Invalid structure for  sd_1210175
ERROR: Invalid structure for  sd_1925412
ERROR: Invalid structure for  sd_1241787
ERROR: Invalid structure for  sd_1210175
ERROR: Invalid structure for  sd_1925412
ERROR: Invalid structure for  sd_1241787
ERROR: Invalid structure for  sd_1210175
ERROR: Invalid structure for  sd_1925412
ERROR: Invalid structure for  sd_1241787
ERROR: Invalid structure for  sd_1210175
ERROR: Invalid structure for  sd_1925412
ERROR: Invalid structure for  sd_1241787
ERROR: Invalid structure for  sd_1925412
ERROR: Invalid structure for  sd_1925412
ERROR: Invalid structure for  sd_1925412
ERROR: Invalid structure for  sd_1925412
ERROR: Invalid structure for  sd_1241787
ERROR: Invalid structure for  sd_1210175
ERROR: Invalid s

/usr/local/lib/python3.12/dist-packages/pymatgen/core/structure.py:3109: UserWarning:

Issues encountered while parsing CIF: 4 fractional coordinates rounded to ideal values to avoid issues with finite precision.
No structure parsed for section 1 in CIF.
'_atom_site_label'
No _symmetry_equiv_pos_as_xyz type key found. Spacegroup from _symmetry_space_group_name_H-M used.
No _symmetry_equiv_pos_as_xyz type key found. Spacegroup from _symmetry_space_group_name_H-M used.
No _symmetry_equiv_pos_as_xyz type key found. Defaulting to P1.



In [262]:
df["Volume_manual"]=df["a, A"]*df["b, A"]*df["c, A"]
df['Valence Electrons Density_manual'] = (df['Valence electrons'] * df['Z']) / df['Volume_manual']

##Oxygen concentration

In [263]:
def count_oxigen(formula):
  #match = re.search(r'O(\d+)', hill_formula)
  #if match:
  #  number = int(match.group(1))
  #  print(number)
  #  return number
  #else:
  #  print("No match found")
  if formula is None:
    return 0
  print(formula)
  comp = Composition(formula)

  # Get number of oxygen atoms
  oxygen_count = comp.get_el_amt_dict().get("O", 0)
  print(oxygen_count)
  return oxygen_count

In [264]:
df['Oxygen_count']=df['Hill formula'].apply(count_oxigen)

K4 Nb6 O17
17.0
K La Nb2 O7
7.0
La Nb2 O7 Rb
7.0
Cs La Nb2 O7
7.0
Ca2 K Nb3 O10
10.0
Ca2 Nb3 O10 Rb
10.0
Ca2 Cs Nb3 O10
10.0
K Nb3 O10 Sr2
10.0
K4 Nb6 O17
17.0
K La Nb2 O7
7.0
La Nb2 O7 Rb
7.0
Cs La Nb2 O7
7.0
Ca2 K Nb3 O10
10.0
Ca2 Nb3 O10 Rb
10.0
Ca2 Cs Nb3 O10
10.0
K Nb3 O10 Sr2
10.0
O2 Ti
2.0
H4 Nb6 O17
17.0
H La Nb2 O7
7.0
H La Nb2 O7
7.0
H La Nb2 O7
7.0
Ca2 H Nb3 O10
10.0
Ca2 H Nb3 O10
10.0
Ca2 H Nb3 O10
10.0
H Nb3 O10 Sr2
10.0
H4 Nb6 O17
17.0
H La Nb2 O7
7.0
H La Nb2 O7
7.0
H La Nb2 O7
7.0
Ca2 H Nb3 O10
10.0
Ca2 H Nb3 O10
10.0
Ca2 H Nb3 O10
10.0
H Nb3 O10 Sr2
10.0
K4 Nb6 O17
17.0
K2 Nb6 O16
16.0
K Nb O3
3.0
K4 Nb6 O17
17.0
K4 Nb6 O17
17.0
K4 Nb6 O17
17.0
K4 Nb6 O17
17.0
K4 Nb6 O17
17.0
La O7 Rb Ta2
7.0
O7 Pr Rb Ta2
7.0
Nd O7 Rb Ta2
7.0
O7 Rb Sm Ta2
7.0
La O7 Rb Ta2
7.0
O7 Pr Rb Ta2
7.0
Nd O7 Rb Ta2
7.0
O7 Rb Sm Ta2
7.0
O2 Ti
2.0
Bi2 Ca O9 Ta2
9.0
Bi2 O9 Sr Ta2
9.0
Ba Bi2 O9 Ta2
9.0
Bi2 Ca Nb2 O9
9.0
Bi2 Nb2 O9 Sr
9.0
Ba Bi2 Nb2 O9
9.0
Bi2 Nb O9 Pb W
9.0
Bi2 Nb O9 Pb W
9.0
Bi2 Nb

In [265]:
df['Oxygen_concentration_manual']=df['Z']*df['Oxygen_count']/df['Volume_manual']
df['Oxygen_concentration_MP']=df['Z_MP']*df['Oxygen_count']/df['Volume_MP']
df['Oxygen_concentration_COD']=df['Z_COD']*df['Oxygen_count']/df['Volume_COD']
df['Oxygen_concentration_Springer']=df['Z_Springer']*df['Oxygen_count']/df['Volume_Springer']

##Packing fraction


In [266]:
ionic_radii={"H+":0.02}
difficult_compunds_oxidation_states={
    "Ca Cs Na O10 Ta3":{"Ca":2,"Cs":1,"Na":1,"O":-2,"Ta":5},
    "Fe K2 La2 O10 Ti2":{"Fe":3, "K": 1,"La":3,"O":-2,"Ti":4},
    'Ca2 H Nb O10 Ta':{"Ca":2,"H":1,"Nb": 5,"Ta":5,"O":-2},
    'K2 O10 Sr Ta3':{"K":1,"O":-2,"Sr":2,"Ta":5},
    'H Nb O10 Sr2 Ta':{"H":1,"Nb":5,"O":-2,"Sr":2,"Ta":5},
}

In [267]:
from pymatgen.core import Structure
from pymatgen.analysis.local_env import ValenceIonicRadiusEvaluator
def get_packing_fraction_from_cif(mp_id):
    print(mp_id)
    cif_folder = "/content/drive/MyDrive/University/Artificial intelligence in chemistry/Perovskite project/Perovskite-liked-oxides-bandgap-prediction/Data/CIF/"
    cif_path = os.path.join(cif_folder, f"{mp_id}.cif")

    if not os.path.isfile(cif_path):
        return np.nan  # Return NaN if file doesn't exist
    try:
      structure = Structure.from_file(cif_path)
    except:
      return 0
    comp = structure.composition
    #comp_oxi = comp.oxidation_state_guesses()
    #print(comp_oxi)


    # Extract radius for each site
    site_radii = []

    try:
      print('Calculating oxidation states')
      structure.add_oxidation_state_by_guess()
    except:
      print('Error')
      return


    for site in structure:
        #el = Element(site.species_string)
        try:
          specie = site.specie
        except AttributeError:
          return 0
        print(site.specie.ionic_radii)
        print(site.specie.oxi_state)
        print('Specie ionic radii ',site.specie.ionic_radii)
        print('Site oxi satte ',site.specie.oxi_state)
        rad =site.specie.ionic_radii.get(site.specie.oxi_state)
        print('got site')
        if(rad is not None):
          site_radii.append(rad)

    # Compute atomic volume per site
    atom_volumes = [(4/3) * np.pi * r**3 for r in site_radii]
    total_atom_volume = sum(atom_volumes)

    # Compute packing fraction
    packing_fraction = total_atom_volume / structure.volume
    print('OK')
    return packing_fraction
    #except:
        #return np.nan  # Return NaN if anything fails (e.g., missing radii)

In [268]:
from pymatgen.core import Structure
from pymatgen.analysis.local_env import ValenceIonicRadiusEvaluator
from pymatgen.core.periodic_table import Species

unresolved_compunds = []

def get_packing_fraction_from_formula_and_cell_volume(hill_formula, V, Z):
    if V==0 or np.isnan(V) or Z==0 or np.isnan(Z):
        return np.nan
    print("Enter!")
    print(hill_formula)
    print(V)
    print(Z)
    comp = Composition(hill_formula)
    oxi_guesses = comp.oxi_state_guesses()
    if(len(oxi_guesses)==0):
      oxi_guesses = difficult_compunds_oxidation_states.get(hill_formula)
      if(oxi_guesses==None):
        unresolved_compunds.append(hill_formula)
        return np.nan
    else:
      oxi_guesses = oxi_guesses[0]

    V_ions_formula=0
    for el, amt in comp.items():
        symbol = el.symbol
        el_oxidation_state = oxi_guesses[symbol]
        #element = Element(el)
        print("Element:", symbol)
        print("Element ox state:", el_oxidation_state)
        specie = Species(symbol,el_oxidation_state)
        r = specie.ionic_radius
        if(r==np.nan or r==None):
          ion_formula = symbol
          if(el_oxidation_state!=0 and el_oxidation_state!=1 and el_oxidation_state!=-1):
             ion_formula =  ion_formula+str(el_oxidation_state)
          if(el_oxidation_state>0):
            ion_formula =  ion_formula+str("+")
          if(el_oxidation_state<0):
            ion_formula =  ion_formula+str("-")
          print("Local ionic radii table request for ",ion_formula)
          r= ionic_radii.get(ion_formula)
          if(r==None):
            r=0
        print("r: ", r)
        V_ion = (4/3) * np.pi * r**3
        V_ions_formula += (V_ion*amt)
        print(el," ",amt)

    packing_fraction= Z*V_ions_formula/V
    return packing_fraction
    print("Output!")

In [269]:
#fr = get_packing_fraction_from_formula_and_cell_volume("H2 La2 Ti3 O10",390.7,2)
#print("Fraction: ", fr)

#fr = get_packing_fraction_from_formula_and_cell_volume("O2 Ti",1183,30)
#print("Fraction: ", fr)

fr = get_packing_fraction_from_formula_and_cell_volume("Ca Cs Na O10 Ta3",228,1)
print("Fraction: ", fr)

Enter!
Ca Cs Na O10 Ta3
228
1
Element: Ca
Element ox state: 2
r:  1.14 ang
Ca   1.0
Element: Cs
Element ox state: 1
r:  1.81 ang
Cs   1.0
Element: Na
Element ox state: 1
r:  1.16 ang
Na   1.0
Element: O
Element ox state: -2
r:  1.26 ang
O   10.0
Element: Ta
Element ox state: 5
r:  0.78 ang
Ta   3.0
Fraction:  0.5584979567677797


In [270]:
#df["MP_packing_fraction"] = df["Materials Project ID"].apply(get_packing_fraction_from_cif)
#df["COD_packing_fraction"] = df["COD_ID"].apply(get_packing_fraction_from_cif)
#df["Springer_packing_fraction"] = df["Springer_ID"].apply(get_packing_fraction_from_cif)

df["MP_packing_fraction"] = df.apply(lambda row: get_packing_fraction_from_formula_and_cell_volume(row["Hill formula"], row["Volume_MP"], row["Z_MP"]), axis=1)
df["COD_packing_fraction"] = df.apply(lambda row: get_packing_fraction_from_formula_and_cell_volume(row["Hill formula"], row["Volume_COD"], row["Z_COD"]), axis=1)
df["Springer_packing_fraction"] = df.apply(lambda row: get_packing_fraction_from_formula_and_cell_volume(row["Hill formula"], row["Volume_Springer"], row["Z_Springer"]), axis=1)
df["Manual_packing_fraction"] = df.apply(lambda row: get_packing_fraction_from_formula_and_cell_volume(row["Hill formula"], row["Volume_manual"], row["Z"]), axis=1)

Enter!
K4 Nb6 O17
1767.044971879869
4.0
Element: K
Element ox state: 1.0
r:  1.52 ang
K   4.0
Element: Nb
Element ox state: 5.0
r:  0.78 ang
Nb   6.0
Element: O
Element ox state: -2.0
r:  1.26 ang
O   17.0
Enter!
K La Nb2 O7
173.54502164551985
1.0
Element: K
Element ox state: 1.0
r:  1.52 ang
K   1.0
Element: La
Element ox state: 3.0
r:  1.172 ang
La   1.0
Element: Nb
Element ox state: 5.0
r:  0.78 ang
Nb   2.0
Element: O
Element ox state: -2.0
r:  1.26 ang
O   7.0
Enter!
La Nb2 O7 Rb
349.00875366799966
2.0
Element: La
Element ox state: 3.0
r:  1.172 ang
La   1.0
Element: Nb
Element ox state: 5.0
r:  0.78 ang
Nb   2.0
Element: O
Element ox state: -2.0
r:  1.26 ang
O   7.0
Element: Rb
Element ox state: 1.0
r:  1.66 ang
Rb   1.0
Enter!
Cs La Nb2 O7
179.6799083471451
1.0
Element: Cs
Element ox state: 1.0
r:  1.81 ang
Cs   1.0
Element: La
Element ox state: 3.0
r:  1.172 ang
La   1.0
Element: Nb
Element ox state: 5.0
r:  0.78 ang
Nb   2.0
Element: O
Element ox state: -2.0
r:  1.26 ang
O   7

/tmp/ipython-input-1623332607.py:32: UserWarning:

No ionic radius for H+!

/tmp/ipython-input-1623332607.py:32: UserWarning:

No ionic radius for Ta4.67+!

/tmp/ipython-input-1623332607.py:32: UserWarning:

No ionic radius for Ta4.33+!

/tmp/ipython-input-1623332607.py:32: UserWarning:

No ionic radius for Zr2+!



r:  0.78 ang
Ta   3.0
Enter!
K4 Nb2 O17 Ta4
1767.044971879869
4.0
Element: K
Element ox state: 1.0
r:  1.52 ang
K   4.0
Element: Nb
Element ox state: 5.0
r:  0.78 ang
Nb   2.0
Element: O
Element ox state: -2.0
r:  1.26 ang
O   17.0
Element: Ta
Element ox state: 5.0
r:  0.78 ang
Ta   4.0
Enter!
K4 O17 Ta6
1767.044971879869
4.0
Element: K
Element ox state: 1.0
r:  1.52 ang
K   4.0
Element: O
Element ox state: -2.0
r:  1.26 ang
O   17.0
Element: Ta
Element ox state: 5.0
r:  0.78 ang
Ta   6.0
Enter!
Nb6 O17 Rb4
1767.044971879869
4.0
Element: Nb
Element ox state: 5.0
r:  0.78 ang
Nb   6.0
Element: O
Element ox state: -2.0
r:  1.26 ang
O   17.0
Element: Rb
Element ox state: 1.0
r:  1.66 ang
Rb   4.0
Enter!
Nb4 O17 Rb4 Ta2
1767.044971879869
4.0
Element: Nb
Element ox state: 5.0
r:  0.78 ang
Nb   4.0
Element: O
Element ox state: -2.0
r:  1.26 ang
O   17.0
Element: Rb
Element ox state: 1.0
r:  1.66 ang
Rb   4.0
Element: Ta
Element ox state: 5.0
r:  0.78 ang
Ta   2.0
Enter!
Nb3 O17 Rb4 Ta3
1767.

/tmp/ipython-input-1623332607.py:32: UserWarning:

No default ionic radius for Ni4+. Using ls data.



r:  0.745 ang
Ti   1.0
Enter!
K4 Nb6 O17
1767.044971879869
4.0
Element: K
Element ox state: 1.0
r:  1.52 ang
K   4.0
Element: Nb
Element ox state: 5.0
r:  0.78 ang
Nb   6.0
Element: O
Element ox state: -2.0
r:  1.26 ang
O   17.0
Enter!
Ba2 K O10 Ta3
240.4062359998148
1.0
Element: Ba
Element ox state: 2.0
r:  1.49 ang
Ba   2.0
Element: K
Element ox state: 1.0
r:  1.52 ang
K   1.0
Element: O
Element ox state: -2.0
r:  1.26 ang
O   10.0
Element: Ta
Element ox state: 5.0
r:  0.78 ang
Ta   3.0
Enter!
Nb O7 Sr2 Ta
309.4413886375399
1.0
Element: Nb
Element ox state: 5.0
r:  0.78 ang
Nb   1.0
Element: O
Element ox state: -2.0
r:  1.26 ang
O   7.0
Element: Sr
Element ox state: 2.0
r:  1.32 ang
Sr   2.0
Element: Ta
Element ox state: 5.0
r:  0.78 ang
Ta   1.0
Enter!
Nb O7 Sr2 Ta
309.4413886375399
1.0
Element: Nb
Element ox state: 5.0
r:  0.78 ang
Nb   1.0
Element: O
Element ox state: -2.0
r:  1.26 ang
O   7.0
Element: Sr
Element ox state: 2.0
r:  1.32 ang
Sr   2.0
Element: Ta
Element ox state: 5.

...

/tmp/ipython-input-1623332607.py:32: UserWarning:

No ionic radius for C2-!

/tmp/ipython-input-1623332607.py:32: UserWarning:

No ionic radius for C2.33-!



Element: C
Element ox state: -2.0
Local ionic radii table request for  C-2.0-
r:  0
C   6.0
Element: H
Element ox state: 1.0
Local ionic radii table request for  H+
r:  0.02
H   16.0
Element: La
Element ox state: 3.0
r:  1.172 ang
La   1.0
Element: N
Element ox state: -3.0
r:  1.32 ang
N   1.0
Element: O
Element ox state: -2.0
r:  1.26 ang
O   4.0
Element: Ti
Element ox state: 4.0
r:  0.745 ang
Ti   1.0
Enter!
C H5 La O5 Ti
446.98032
4.0
Element: C
Element ox state: -2.0
Local ionic radii table request for  C-2.0-
r:  0
C   1.0
Element: H
Element ox state: 1.0
Local ionic radii table request for  H+
r:  0.02
H   5.0
Element: La
Element ox state: 3.0
r:  1.172 ang
La   1.0
Element: O
Element ox state: -2.0
r:  1.26 ang
O   5.0
Element: Ti
Element ox state: 4.0
r:  0.745 ang
Ti   1.0
Enter!
C2 H7 La O5 Ti
506.4854400000001
4.0
Element: C
Element ox state: -2.0
Local ionic radii table request for  C-2.0-
r:  0
C   2.0
Element: H
Element ox state: 1.0
Local ionic radii table request for  H

/tmp/ipython-input-1623332607.py:32: UserWarning:

No ionic radius for C1.33-!



Element: C
Element ox state: -2.0
Local ionic radii table request for  C-2.0-
r:  0
C   8.0
Element: H
Element ox state: 1.0
Local ionic radii table request for  H+
r:  0.02
H   19.0
Element: Ca
Element ox state: 2.0
r:  1.14 ang
Ca   2.0
Element: Nb
Element ox state: 5.0
r:  0.78 ang
Nb   3.0
Element: O
Element ox state: -2.0
r:  1.26 ang
O   11.0
Enter!
Ca2 K Nb3 O10
438.04823999999996
2.0
Element: Ca
Element ox state: 2.0
r:  1.14 ang
Ca   2.0
Element: K
Element ox state: 1.0
r:  1.52 ang
K   1.0
Element: Nb
Element ox state: 5.0
r:  0.78 ang
Nb   3.0
Element: O
Element ox state: -2.0
r:  1.26 ang
O   10.0
Enter!
Ca2 H Nb3 O10
233.4784
1.0
Element: Ca
Element ox state: 2.0
r:  1.14 ang
Ca   2.0
Element: H
Element ox state: 1.0
Local ionic radii table request for  H+
r:  0.02
H   1.0
Element: Nb
Element ox state: 5.0
r:  0.78 ang
Nb   3.0
Element: O
Element ox state: -2.0
r:  1.26 ang
O   10.0
Enter!
C H5 Ca2 Nb3 O11
311.40164
1.0
Element: C
Element ox state: -2.0
Local ionic radii t

/tmp/ipython-input-1623332607.py:32: UserWarning:

No default ionic radius for Mn4+. Using ls data.



In [271]:
print(unresolved_compunds)

['Ca2 K Nb2 O10 Rh', 'Ca2 H Nb2 O10 Rh', 'Ca2 H Nb2 O10 Rh', 'Ca2 H Nb2 O10 Rh', 'Ca2 H Nb2 O10 Rh', 'Ca2 H Nb2 O10 Rh', 'Ca2 K Nb2 O10 Rh', 'Ca2 H Nb2 O10 Rh', 'Ca2 H Nb2 O10 Rh', 'Ca2 H Nb2 O10 Rh', 'Ca2 H Nb2 O10 Rh', 'Ca2 H Nb2 O10 Rh']


##Averaging


In [272]:
def averaging_valence_electron_density(MP,COD,Springer):
  sum=0;
  count=0;
  print(MP)
  print(COD)
  print(Springer)
  if(pd.notna(MP)):
    sum+=MP
    count+=1
  if(pd.notna(COD)):
    sum+=COD
    count+=1
  if(pd.notna(Springer)):
    sum+=Springer
    count+=1
  print('Count: ',count)
  if count==0:
    return 0
  return sum/count


def averaging_4(MP,COD,Springer,manual):
  sum=0;
  count=0;
  print(MP)
  print(COD)
  print(Springer)
  print(manual)
  if(pd.notna(MP)):
    sum+=MP
    count+=1
  if(pd.notna(COD)):
    sum+=COD
    count+=1
  if(pd.notna(Springer)):
    sum+=Springer
    count+=1
  if(pd.notna(manual)):
    sum+=manual
    count+=1
  print('Count: ',count)
  if count==0:
    print("No value")
    return np.nan
  return sum/count

In [273]:
df['Valence Electrons Density avg'] = df.apply(lambda x: averaging_4(x['Valence Electrons Density_MP'], x['Valence Electrons Density_COD'],x['Valence Electrons Density_Springer'],x['Valence Electrons Density_manual']), axis=1)
df['Oxygen_concentration avg'] = df.apply(lambda x: averaging_4(x['Oxygen_concentration_MP'], x['Oxygen_concentration_COD'],x['Oxygen_concentration_Springer'],x['Oxygen_concentration_manual']), axis=1)
df['Packing fraction avg'] = df.apply(lambda x: averaging_4(x['MP_packing_fraction'], x['COD_packing_fraction'],x['Springer_packing_fraction'],x['Manual_packing_fraction']), axis=1)

0.07696465124784942
0.08096100367603028
nan
0.07700954714535801
Count:  3
0.08067070934824143
0.042674323496713386
nan
0.08686837001574316
Count:  3
0.0802272140905539
nan
nan
0.08440881746619917
Count:  2
0.07791633538098053
0.08214000614035505
nan
0.08208238574318606
Count:  3
0.08651015304565358
0.09057669425458144
nan
0.09094461183266286
Count:  3
0.08319251751861964
0.09008620157303462
nan
0.08991755641195143
Count:  3
0.08410254452742943
0.08841182372752909
nan
0.022201202381538672
Count:  3
0.08651015304565358
nan
nan
0.08701336922366086
Count:  2
0.07696465124784942
0.08096100367603028
nan
0.07700954714535801
Count:  3
0.08067070934824143
0.042674323496713386
nan
0.08686837001574316
Count:  3
0.0802272140905539
nan
nan
0.08440881746619917
Count:  2
0.07791633538098053
0.08214000614035505
nan
0.08208238574318606
Count:  3
0.08651015304565358
0.09057669425458144
nan
0.09094461183266286
Count:  3
0.08319251751861964
0.09008620157303462
nan
0.08991755641195143
Count:  3
0.084102544

In [274]:
df.to_excel('checkpoint_before_CIF_embeddings.xlsx')

##CIF embedings

In [275]:
from pymatgen.core import Structure
from matminer.featurizers.site import CrystalNNFingerprint
from matminer.featurizers.structure import SiteStatsFingerprint
from pymatgen.transformations.standard_transformations import OrderDisorderedStructureTransformation
from matminer.featurizers.structure import JarvisCFID
from matminer.featurizers.structure import RadialDistributionFunction
from matminer.featurizers.structure.rdf import ElectronicRadialDistributionFunction


In [276]:
matgl.get_available_pretrained_models()

['CHGNet-MPtrj-2023.12.1-2.7M-PES',
 'CHGNet-MPtrj-2024.2.13-11M-PES',
 'CHGNet-MatPES-PBE-2025.2.10-2.7M-PES',
 'CHGNet-MatPES-r2SCAN-2025.2.10-2.7M-PES',
 'M3GNet-ANI-1x-Subset-PES',
 'M3GNet-MP-2018.6.1-Eform',
 'M3GNet-MP-2021.2.8-DIRECT-PES',
 'M3GNet-MP-2021.2.8-PES',
 'M3GNet-MatPES-PBE-v2025.1-PES',
 'M3GNet-MatPES-r2SCAN-v2025.1-PES',
 'M3GNet-r2SCAN-NaBH',
 'MEGNet-MP-2018.6.1-Eform',
 'MEGNet-MP-2019.4.1-BandGap-mfi',
 'QET-MatQ-PES',
 'SO3Net-ANI-1x-Subset-PES',
 'TensorNet-ANI-1x-Subset-PES',
 'TensorNet-MatPES-PBE-v2025.1-PES',
 'TensorNet-MatPES-r2SCAN-v2025.1-PES',
 'TensorNetDGL-MatPES-PBE-v2025.1-PES',
 'TensorNetDGL-MatPES-r2SCAN-v2025.1-PES']

In [277]:
model = matgl.load_model("MEGNet-MP-2019.4.1-BandGap-mfi")
state_attr = torch.tensor([0], dtype=torch.long)
output = model.predict_structure(struct, state_attr=state_attr)
print(output)

/usr/local/lib/python3.12/dist-packages/matgl/utils/io.py:159: UserWarning:

Incompatible model version detected! The code will continue to load the model but it is recommended that you provide a path to an updated model, increment your @model_version in model.json if you are confident that the changes are not problematic, or clear your ~/.matgl cache using `python -c "import matgl; matgl.clear_cache()"`



NameError: name 'torch' is not defined

In [ ]:
from matgl.ext._pymatgen_dgl import Structure2Graph

converter = Structure2Graph(
    element_types=['Cs','Cl'],   # or explicit list like ["H", "C", "O", ...]
    cutoff=4.0            # must match model cutoff!
)

#g, lattice, state_attr = converter.get_graph(struct)
#output = model.forward(g,state_attr=state_attr)

In [ ]:
model = matgl.load_model("M3GNet-MP-2018.6.1-Eform")
#model = matgl.load_model("MEGNet-MP-2019.4.1-BandGap-mfi")
eform = model.predict_structure(struct)
print(f"The predicted formation energy for CsCl is {float(eform):.3f} eV/atom.")

# Extract the structure features of a structure
feat_dict = model.model.predict_structure(struct, return_features=True)
# Print out structure-wise features, it should be the dimension of node_features * 2 from set2set layer
print(feat_dict["readout"].shape)


In [278]:
embedding_length = {
    'M3GNet':128,
    'SiteStatsFingerprint':122,
    'RDF':200,
    'CGCNN':1000,
    'electronic_RDF':200}


model = matgl.load_model("M3GNet-MP-2018.6.1-Eform")
jarvis = JarvisCFID() #122
featurizer_rdf = RadialDistributionFunction() #200
#featurizer_CGCNNF = dc.feat.CGCNNFeaturizer()
featurizer_electronic_rdf = ElectronicRadialDistributionFunction() #401 integer values

site_fp = CrystalNNFingerprint.from_preset("ops")
structure_featurizer = SiteStatsFingerprint(site_featurizer=site_fp)  #122

def extract_embedings_from_CIF(cif_file):
  if(embedding_type=='None'):
    return None
  #cif_folder = "/content/drive/MyDrive/University/Artificial intelligence in chemistry/Perovskite project/Perovskite-liked-oxides-bandgap-prediction/Data/CIF/"
  cif_path = os.path.join(cif_folder, f"{cif_file}.cif")
  structure = Structure.from_file(cif_path)

  embedding= [None] * embedding_length[embedding_type]

  #structure.add_oxidation_state_by_guess()
  if structure.is_ordered:
        #structure.add_oxidation_state_by_guess()  # improves CrystalNN
        #embedding = structure_featurizer.featurize(structure)
        #embedding = featurizer_rdf.featurize(structure)
        #embedding = featurizer_CGCNNF.featurize(structure)
        #embedding =  featurizer_electronic_rdf.featurize(structure)
        #print(embedding)
        if(embedding_type=='M3GNet'):
          embedding = model.model.predict_structure(structure, return_features=True)
          embedding = embedding["readout"].detach().cpu().flatten().tolist()
        if(embedding_type=='SiteStatsFingerprint'):
          embedding = structure_featurizer.featurize(structure)
        if(embedding_type=='RDF'):
          embedding = featurizer_rdf.featurize(structure)
        if(embedding_type=='CGCNN'):
          embedding = None# featurizer_CGCNNF.featurize(structure)
        if(embedding_type=='electronic_RDF'):
          embedding = featurizer_rdf.featurize(structure)
  else:
       # df.at[idx, "disordered_structure"] = True
       # df.at[idx, "embedding"] = None  # cannot featurize
       print(f"Skipped structure-based features for {cif_ID} (disordered)")

  #embedding = structure_featurizer.featurize(structure)

  #embedding = jarvis.featurize(structure)
  print(len(embedding))
  print('Final: ',embedding)
  return embedding

In [279]:
extract_embedings_from_CIF("mp-1245098")
extract_embedings_from_CIF("M_MP98")
#raise SystemExit("Stopping execution")

200
Final:  [  0.           0.           0.           0.           0.
   0.           0.           0.           0.           0.
   0.           0.           0.           0.           0.
   0.           0.          68.27679287 384.90958879 159.47807246
 144.30172933  67.85836984  16.52307377   3.78674548  41.80768861
  48.24170116 101.25185904 113.38040011 121.01270063 127.36720607
 101.16756608 103.27753644  73.26020158  72.67919612  84.34124579
  92.93300366  80.06167138 105.59356383  70.54910349 100.53360283
  93.08037398  71.64768698  94.94745446  79.57968699 100.33505136
  79.80942584  91.89001698 103.82026498  95.13762042  93.03978532
  93.49217726  88.31963977  95.6106295   95.72347522  95.05959272
  90.30697503  87.79381784 107.53990675  81.28243462  83.89026378
  77.71156252  87.37046689  76.03024931  88.17792304  93.50873578
  84.82533479  85.13113045 101.44815535  96.27915388  85.30146582
  87.94843997  92.86970458  92.31503871  94.07890759  99.10693656
  81.08852322  91.4909

array([ 0.        ,  0.        ,  0.        ,  0.        ,  0.        ,
        0.        ,  0.        ,  0.        ,  0.        ,  0.        ,
        0.        ,  0.        ,  0.        ,  0.        ,  0.        ,
        0.        ,  0.        ,  0.        , 13.97097401, 37.72530316,
       45.51368851,  0.        ,  0.        ,  8.65913718,  0.        ,
       29.41709955,  0.        , 25.29429758, 82.42702677, 21.98114179,
       23.13395069, 19.27872396,  0.        ,  0.        , 16.07190177,
        0.        , 14.35895952,  0.        ,  6.45297518, 50.57576159,
        0.        ,  2.77688994, 10.5910244 , 32.85652174, 38.64181869,
       10.39556535,  0.        , 50.87259082, 34.56415405, 31.2299068 ,
        3.75067058,  7.2128643 ,  0.        ,  1.67092003,  0.        ,
       12.42133129, 32.96023668,  5.78614389, 33.54013512, 13.50926495,
        7.83982714, 21.49636337, 40.40364195, 16.60532895, 18.39364192,
        8.91815107, 13.51868386,  0.        , 10.1926478 , 11.88

In [280]:
if(embedding_type is not 'None'):
  df["embedding"] = [None] * len(df)

  for idx, row in df.iterrows():
      cif_ID = 0
      if(row['Materials Project verification']):
        cif_ID = row['MP_CIF_modified']
      elif(row['COD verification']):
        cif_ID = row['COD_CIF_modified']
      elif(row['Springer verification']):
        cif_ID = row['Springer_CIF_modified']
      else:
        raise SystemExit("Stopping execution")
      print('CIF: ', cif_ID)
      #cif_path = os.path.join(cif_folder, f"{cif_ID}.cif")
      #structure = Structure.from_file(cif_path)

      embedding= extract_embedings_from_CIF(cif_ID)
      print('Insert embedding: ', embedding)
      df.at[idx, "embedding"] = embedding

CIF:  mp-560692


<>:1: SyntaxWarning:

"is not" with 'str' literal. Did you mean "!="?

<>:1: SyntaxWarning:

"is not" with 'str' literal. Did you mean "!="?

/tmp/ipython-input-1239243898.py:1: SyntaxWarning:

"is not" with 'str' literal. Did you mean "!="?



200
Final:  [  0.           0.           0.           0.           0.
   0.           0.           0.           0.           0.
   0.           0.           0.           0.           0.
   0.           0.          34.00241107 152.13347503 273.86692175
 272.58554598  67.58806584  41.14314124  56.57492294   0.
  16.01651244 133.47600472 234.12061177 115.40169961 371.00524278
 134.35277293  73.47581807  88.74532721 120.64948174  35.00220193
  16.52907473  78.17917381 111.09818359 126.48254641 106.80868454
 126.99945447 114.90538023 103.7955128   77.06095135 115.7146519
 100.62217283  86.70693447 175.42210065  84.13151476 114.77374858
 163.36800821 129.59546568 120.92670271  83.69732884  98.18763793
  81.15541375  94.62235119  63.00678651  70.00184696 111.80041421
  88.21552581 104.64723709 130.65641887 157.57139473 105.15383883
  94.68420597 150.74137404 109.73109642  91.01206554  97.0374515
  83.82594265  83.53503597  93.136289    86.76310913 118.22939124
 124.25464432 138.82558695 117.9

/usr/local/lib/python3.12/dist-packages/pymatgen/core/structure.py:3109: UserWarning:

No structure parsed for section 1 in CIF.
'_atom_site_label'

/usr/local/lib/python3.12/dist-packages/pymatgen/io/cif.py:1029: UserWarning:

No _symmetry_equiv_pos_as_xyz type key found. Spacegroup from _symmetry_space_group_name_H-M used.

/usr/local/lib/python3.12/dist-packages/pymatgen/io/cif.py:1314: UserWarning:

Cannot determine chemical composition from CIF! 'NoneType' object is not iterable

/usr/local/lib/python3.12/dist-packages/pymatgen/io/cif.py:1029: UserWarning:

No _symmetry_equiv_pos_as_xyz type key found. Defaulting to P1.

/usr/local/lib/python3.12/dist-packages/pymatgen/core/structure.py:3109: UserWarning:

Issues encountered while parsing CIF: No structure parsed for section 1 in CIF.
'_atom_site_label'
No _symmetry_equiv_pos_as_xyz type key found. Spacegroup from _symmetry_space_group_name_H-M used.
No _symmetry_equiv_pos_as_xyz type key found. Spacegroup from _symmetry_space_gro

200
Final:  [  0.           0.           0.           0.           0.
   0.           0.           0.           0.           0.
   0.           0.           0.           0.           0.
   0.           0.          34.00241107 152.13347503 273.86692175
 272.58554598  67.58806584  41.14314124  56.57492294   0.
  16.01651244 133.47600472 234.12061177 115.40169961 371.00524278
 134.35277293  73.47581807  88.74532721 120.64948174  35.00220193
  16.52907473  78.17917381 111.09818359 126.48254641 106.80868454
 126.99945447 114.90538023 103.7955128   77.06095135 115.7146519
 100.62217283  86.70693447 175.42210065  84.13151476 114.77374858
 163.36800821 129.59546568 120.92670271  83.69732884  98.18763793
  81.15541375  94.62235119  63.00678651  70.00184696 111.80041421
  88.21552581 104.64723709 130.65641887 157.57139473 105.15383883
  94.68420597 150.74137404 109.73109642  91.01206554  97.0374515
  83.82594265  83.53503597  93.136289    86.76310913 118.22939124
 124.25464432 138.82558695 117.9

...

200
Final:  [  0.           0.           0.           0.           0.
   0.           0.           0.           0.           0.
   0.           0.           0.           0.           0.
   0.           0.           0.          41.08168766  36.9771194
   0.          30.41881271  27.77543991   0.           0.
   0.           0.          37.18897596 121.18844998 129.27121633
  15.11676576  14.17228526  13.31362992   0.           0.
  11.15865994  31.66692011  11.66691367  12.64999422   0.
  25.72092658  32.66181013  23.35720238  11.14784919  14.20329683
  33.96465403  39.02348688  12.46591616   5.97858768  40.17633691
 115.80300063  15.90708555  10.20459384  24.56672483   0.
   0.          13.21631823  40.4086587   49.31243      0.
  13.4476028   29.74593689  21.60127651  17.43857701  50.70614522
  36.05779081   6.36027636  15.43305773  14.9857545   18.92490553
  16.97708801  30.2601438   22.74225331  19.52438448  20.27068319
  30.83949274  40.85237711  90.14647813   9.1287701    8.900562

/usr/local/lib/python3.12/dist-packages/pymatgen/core/structure.py:3109: UserWarning:

Issues encountered while parsing CIF: Pauling file corrections applied.
Pauling file corrections applied.
No structure parsed for section 1 in CIF.
'_atom_site_label'
No _symmetry_equiv_pos_as_xyz type key found. Spacegroup from _symmetry_space_group_name_H-M used.
No _symmetry_equiv_pos_as_xyz type key found. Spacegroup from _symmetry_space_group_name_H-M used.
No _symmetry_equiv_pos_as_xyz type key found. Defaulting to P1.



Streaming output truncated to the last 5000 lines.
200
Final:  [  0.           0.           0.           0.           0.
   0.           0.           0.           0.           0.
   0.           0.           0.           0.           0.
   0.           0.           0.           0.           0.
 119.09983471   0.          32.95696545   0.           0.
   0.          71.2790183   66.18990373   0.          57.52006571
   0.          25.2242008    0.           0.           0.
   0.           0.         106.79181671  33.7721816    0.
  15.25959069   7.26654207  55.42900593  26.45497473  25.27939599
  76.57148446   0.           0.          21.28169074   0.
   0.           0.          27.24360108  52.46939265  33.70775257
   0.          47.04549177  15.14113233  14.6279236   14.14037205
   0.          26.47129489  12.81550402  27.9338684   96.26465287
  11.6684711    0.          21.97452507  24.89389882  20.72802313
   0.          19.5846504   19.04811866  13.9000023   67.64678919
   0.      

/usr/local/lib/python3.12/dist-packages/pymatgen/io/cif.py:1314: UserWarning:

Missing elements K from PMG structure composition



Streaming output truncated to the last 5000 lines.
 802.61014245   0.           0.           0.           0.
 147.386384    48.77551233 187.9016019   51.73592155  69.85029548
 105.33860315 478.84635391   8.74469905  72.14772524 177.01096534
 183.82693088  88.26045088 550.29554809  87.21016238  96.66057422
 257.00203666  17.84776333 205.38866993 138.07897981  48.356643
 147.55205237  49.849379    51.94898427 271.81718125 187.28713066
  56.68505487 246.79446378 100.5002975  239.83226711  26.83022627
 235.25225637 354.24591172  98.11787456  92.23135823  88.54260577
 236.114875   148.57416229  96.38310212 133.03307508 260.86405848
 110.68133698  98.47625017 103.11586199 103.50207739 158.83307861
 277.01050081 122.91669825 187.023436   151.53189256 167.09094332
 115.58683553 130.15871874 130.21790277 122.66929896 175.99710087
 126.49816215 154.16373597 225.75287119 186.86796517  90.94255935
 155.34995448 111.97318921 140.80086524 109.21437087 148.51737492
 174.91377252 182.64647026 153.5253

In [281]:
df.to_excel('checkpoint_cif_embeddings.xlsx')

In [282]:
#df = pd.read_excel('checkpoint_cif_embeddings.xlsx')

#raise SystemExit("Stopping execution")

In [283]:
if(embedding_type is not 'None'):
  df = df[df["embedding"].notna()]
  emb_df = pd.DataFrame(df["embedding"].to_list(), index=df.index)
  emb_df.columns = [f"emb_{i}" for i in range(emb_df.shape[1])]
  df = pd.concat([df, emb_df], axis=1)
  df.drop(columns=["embedding"], inplace=True)


<>:1: SyntaxWarning:

"is not" with 'str' literal. Did you mean "!="?

<>:1: SyntaxWarning:

"is not" with 'str' literal. Did you mean "!="?

/tmp/ipython-input-2088131617.py:1: SyntaxWarning:

"is not" with 'str' literal. Did you mean "!="?



In [284]:
#!pip uninstall ase -y
#!pip install ase==3.22.1
#!pip install m3gnet

In [285]:
if(embedding_type is not 'None'):
  print(df.shape[0])
  df = df.dropna(subset=["emb_0"])
  print(df.shape[0])
  print(df.isna().sum().sum())

663
530
8258


<>:1: SyntaxWarning:

"is not" with 'str' literal. Did you mean "!="?

<>:1: SyntaxWarning:

"is not" with 'str' literal. Did you mean "!="?

/tmp/ipython-input-3843408793.py:1: SyntaxWarning:

"is not" with 'str' literal. Did you mean "!="?



In [286]:
df.to_excel('checkpoint_cif_embeddings_split.xlsx')

In [287]:
#from pymatgen.core import Structure
#from m3gnet.models import M3GNet

#test_cif = "/content/drive/MyDrive/University/Artificial intelligence in chemistry/Perovskite project/Perovskite-liked-oxides-bandgap-prediction/Data/CIF/mp-557195.cif"
#structure = Structure.from_file(test_cif )
#model = M3GNet.load()

#embedding = model.get_structure_embedding(structure)
#print(embedding.shape)

##Augmentation


In [288]:
#df = pd.read_excel('checkpoint_cif_embeddings_split.xlsx')

In [289]:
def proportional_augmentation(_df, x_cols, y_col, alpha):
    augmented = []

    #for _ in range(n_clones):
    #alpha = np.random.uniform(*alpha_range, size=len(_df))
    clone = _df.copy()

    clone[x_cols] = clone[x_cols].multiply(alpha, axis=0)
    clone[y_col] = clone[y_col] * alpha

    augmented.append(clone)

    return pd.concat([_df] + augmented, ignore_index=True)

In [290]:
def proportional_augmentations(_df, x_cols, y_col, n_clones = 5, alpha_range=(1, 5)):
    augmented = []

    for _ in range(n_clones):
      alpha = np.random.uniform(*alpha_range, size=len(_df))
      clone = _df.copy()

      clone[x_cols] = clone[x_cols].multiply(alpha, axis=0)
      clone[y_col] = clone[y_col] * alpha

      augmented.append(clone)

    return pd.concat([_df] + augmented, ignore_index=True)

In [291]:
if(do_augmentation):
  df = proportional_augmentation(df,'Alcohol, %','Rate, umol/(g*h)',2)
  df = proportional_augmentation(df,'Promoter, w%','Rate, umol/(g*h)',2)
  df.info()

#EDA

In [292]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 530 entries, 0 to 1088
Columns: 285 entries, Perovskite to emb_199
dtypes: bool(5), float64(260), object(20)
memory usage: 1.1+ MB


In [293]:
df.columns

Index(['Perovskite', 'Interlayer space composition', 'Bandgap, eV',
       'Materials Project ID', 'COD_ID', 'Springer_ID', 'Z', 'a, A', 'b, A',
       'c, A',
       ...
       'emb_190', 'emb_191', 'emb_192', 'emb_193', 'emb_194', 'emb_195',
       'emb_196', 'emb_197', 'emb_198', 'emb_199'],
      dtype='object', length=285)

In [294]:
columns_EDA = ['Perovskite','Bandgap, eV',
       'Symmetry group', 'd,A', 'Number of octahedrons on a layer',
       'Prep Method', 'CalcT(K)', 'Calc time (h)', 'Nitrogen',
       'Promotion method', 'Promoter', 'Promoter, w%', 'Surface area, m2/g',
       'CatW, g/L', 'Alcohol, %', 'Light type',
       'Power, W', 'Wave length min, nm', 'Cell material', 'Temperature, K',
       'Rate, umol/(g*h)',
       'avg s valence electrons', 'avg p valence electrons',
       'avg d valence electrons', 'avg f valence electrons',
       'frac s valence electrons', 'frac p valence electrons',
       'frac d valence electrons', 'frac f valence electrons',
       'Average Mulliken electronegativity', 'Valence electrons',
       'Valence Electrons Density avg', 'Oxygen_concentration avg',
       'Packing fraction avg','Log_rate']

In [295]:
categorical_cols = [col for col in columns_EDA
                    if df[col].dtype in ['object', 'category','bool']]

numerical_cols = [col for col in columns_EDA
                  if df[col].dtype in ['int64', 'float64']]
print(categorical_cols)
print(numerical_cols)

['Perovskite', 'Symmetry group', 'Prep Method', 'Nitrogen', 'Promotion method', 'Promoter', 'Light type', 'Cell material']
['Bandgap, eV', 'd,A', 'Number of octahedrons on a layer', 'CalcT(K)', 'Calc time (h)', 'Promoter, w%', 'Surface area, m2/g', 'CatW, g/L', 'Alcohol, %', 'Power, W', 'Wave length min, nm', 'Temperature, K', 'Rate, umol/(g*h)', 'avg s valence electrons', 'avg p valence electrons', 'avg d valence electrons', 'avg f valence electrons', 'frac s valence electrons', 'frac p valence electrons', 'frac d valence electrons', 'frac f valence electrons', 'Average Mulliken electronegativity', 'Valence electrons', 'Valence Electrons Density avg', 'Oxygen_concentration avg', 'Packing fraction avg', 'Log_rate']


In [296]:
import plotly.express as px
from scipy.stats import gaussian_kde
import plotly.graph_objects as go

def plot_smooth_distribution(df, column):
    data = df[column].dropna().values

    kde = gaussian_kde(data)
    x_vals = np.linspace(data.min(), data.max(), 500)
    y_vals = kde(x_vals)

    # Plot
    fig = go.Figure()

    fig.add_trace(go.Scatter(
        x=x_vals,
        y=y_vals,
        mode='lines',
        line=dict(width=3),
        name=f'{column} KDE'
    ))

    fig.update_layout(
        title=f"Distribution of '{column}'",
        xaxis_title=column,
        yaxis_title="Density",
        #template="plotly_white"
    )

    fig.show()

In [297]:
plot_smooth_distribution(df, 'Bandgap, eV')

In [298]:
for col in numerical_cols:
    fig = px.histogram(df, x=col, nbins=20, title=f'Histogram of {col}',width=800, height=500)
    fig.show()

In [299]:
def draw_pie_chart(df, column):
  fig = px.pie(df, names=column, title=f'{column} Distribution',hole=0.3)
  fig.update_traces(textinfo='percent+label')
  fig.show()

In [300]:
for col in categorical_cols:
     draw_pie_chart(df,col)

In [301]:
from scipy.stats import pearsonr

def draw_scatter_plot(df,x_column, y_column):
  from sklearn.metrics import r2_score

  x = df[x_column]
  y = df[y_column]

  r, p_value = pearsonr(x, y)

  fig = go.Figure()

  fig.add_trace(go.Scatter(
      x=x,
      y=y,
      mode='markers',
      name='Data',
      marker=dict(size=8, color='blue', opacity=0.7)
  ))

  fig.add_annotation(
    x=np.mean(x),
    y=np.max(y),
    text=f"Pearson r = {r:.3f}",
    showarrow=False,
    font=dict(size=14, color="red")
  )

  fig.update_layout(
      xaxis_title=f'{x_column}',
      yaxis_title=f'{y_column}',
      template="plotly_white",
      width=600,
      height=600,
  )

  fig.show()

In [302]:
for col in numerical_cols:
  draw_scatter_plot(df,col,'Rate, umol/(g*h)')

In [303]:
for col in numerical_cols:
  draw_scatter_plot(df,col,target_col)

df_selected = df[numerical_cols]


In [304]:
def draw_corr_heatmap(_df):
  # Compute correlation matrix
  corr_matrix = _df.corr()

  # Plot heatmap
  fig = px.imshow(
      corr_matrix,
      text_auto=True,        # show correlation values
      aspect="auto",
      color_continuous_scale='RdBu_r',  # diverging color map
      title="Correlation Heatmap",
      width=1000,
      height=1000,
  )
  fig.show()

In [305]:
draw_corr_heatmap(df_selected)

In [306]:
df.to_excel('checkpoint_descriptors.xlsx')

#Preparing data for ML

##Categorization


In [307]:
#raise SystemExit("Stopping execution")

In [308]:
categorical_columns = df.select_dtypes(include='object').columns.tolist()
categorical_columns.remove('Perovskite')
categorical_columns.remove('Interlayer space composition')
categorical_columns.remove('Materials Project ID')
categorical_columns.remove('COD_ID')
categorical_columns.remove('Springer_ID')
categorical_columns.remove('Symmetry group')
categorical_columns.remove('Sac Agent 1')
categorical_columns.remove('Sac agent 2')
categorical_columns.remove('Hill formula')

columns_to_remove = ['MP_CIF_modifier',
 'COD_CIF_modifier',
 'Springer_CIF_modifier',
 'MP_CIF_modified',
 'COD_CIF_modified',
 'Springer_CIF_modified']

for c in columns_to_remove:
  categorical_columns.remove(c)

categorical_columns

['Prep Method', 'Promotion method', 'Promoter', 'Light type', 'Cell material']

In [309]:
df2 = df['Light type'].value_counts()
print(df2.index)

Index(['Hg lamp', 'Xe lamp', 'LED', 'W lamp '], dtype='object', name='Light type')


In [310]:
df[categorical_columns].isna().sum()

Prep Method         0
Promotion method    0
Promoter            0
Light type          0
Cell material       0
dtype: int64

In [311]:
for col in df.columns:
    print(col)

Perovskite
Interlayer space composition
Bandgap, eV
Materials Project ID
COD_ID
Springer_ID
Z
a, A
b, A
c, A
Symmetry group
d,A
Number of octahedrons on a layer
Prep Method
CalcT(K)
Calc time (h)
Nitrogen
Promotion method
Promoter
Promoter, w%
Surface area, m2/g
CatW, g/L
Alcohol, %
Sac Agent 1
Sac agent 2
Light type
Power, W
Wave length min, nm
Cell material
Temperature, K
Rate, umol/(g*h)
MP_CIF_modifier
COD_CIF_modifier
Springer_CIF_modifier
Materials Project verification
COD verification
Springer verification
General verification
MP_CIF_modified
COD_CIF_modified
Springer_CIF_modified
Log_rate
Hill formula
avg s valence electrons
avg p valence electrons
avg d valence electrons
avg f valence electrons
frac s valence electrons
frac p valence electrons
frac d valence electrons
frac f valence electrons
Average Mulliken electronegativity
Valence electrons
Volume_MP
Z_MP
Valence Electrons Density_MP
a_MP
b_MP
c_MP
Volume_COD
Z_COD
Valence Electrons Density_COD
a_COD
b_COD
c_COD
Volume_Spr

In [312]:
df = pd.get_dummies(df, columns=categorical_columns, drop_first=True)
df.columns


Index(['Perovskite', 'Interlayer space composition', 'Bandgap, eV',
       'Materials Project ID', 'COD_ID', 'Springer_ID', 'Z', 'a, A', 'b, A',
       'c, A',
       ...
       'Promoter_NiO', 'Promoter_No promoter', 'Promoter_Pt', 'Promoter_Rh',
       'Promoter_RuO2', 'Promoter_ZnO', 'Light type_LED', 'Light type_W lamp ',
       'Light type_Xe lamp', 'Cell material_quartz'],
      dtype='object', length=303)

In [313]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 530 entries, 0 to 1088
Columns: 303 entries, Perovskite to Cell material_quartz
dtypes: bool(28), float64(260), object(15)
memory usage: 1.1+ MB


In [314]:
columns_for_ML = df.columns
columns_to_exlude = ['Perovskite', 'Interlayer space composition','Materials Project ID', 'COD_ID', 'Springer_ID', 'Z', 'a, A', 'b, A',
       'c, A', 'Symmetry group', 'Number of octahedrons on a layer','Sac Agent 1',
       'Sac agent 2','Rate, umol/(g*h)','Hill formula','Volume_MP', 'Z_MP',
       'Valence Electrons Density_MP', 'a_MP', 'b_MP', 'c_MP', 'Volume_COD',
       'Z_COD', 'Valence Electrons Density_COD', 'a_COD', 'b_COD', 'c_COD',
       'Volume_Springer', 'Z_Springer', 'Valence Electrons Density_Springer',
       'a_Springer', 'b_Springer', 'c_Springer', 'Volume_manual',
       'Valence Electrons Density_manual', 'Oxygen_count',
       'Oxygen_concentration_manual', 'Oxygen_concentration_MP',
       'Oxygen_concentration_COD', 'Oxygen_concentration_Springer',
       'MP_packing_fraction', 'COD_packing_fraction',
       'Springer_packing_fraction', 'Manual_packing_fraction']
columns_to_exlude += ['MP_CIF_modifier',
'COD_CIF_modifier',
'Springer_CIF_modifier',
'Materials Project verification',
'COD verification',
'Springer verification',
'General verification',
'MP_CIF_modified',
'COD_CIF_modified',
'Springer_CIF_modified',]

columns_for_ML = [x for x in columns_for_ML if x not in columns_to_exlude]
print(columns_for_ML)


['Bandgap, eV', 'd,A', 'CalcT(K)', 'Calc time (h)', 'Nitrogen', 'Promoter, w%', 'Surface area, m2/g', 'CatW, g/L', 'Alcohol, %', 'Power, W', 'Wave length min, nm', 'Temperature, K', 'Log_rate', 'avg s valence electrons', 'avg p valence electrons', 'avg d valence electrons', 'avg f valence electrons', 'frac s valence electrons', 'frac p valence electrons', 'frac d valence electrons', 'frac f valence electrons', 'Average Mulliken electronegativity', 'Valence electrons', 'Valence Electrons Density avg', 'Oxygen_concentration avg', 'Packing fraction avg', 'emb_0', 'emb_1', 'emb_2', 'emb_3', 'emb_4', 'emb_5', 'emb_6', 'emb_7', 'emb_8', 'emb_9', 'emb_10', 'emb_11', 'emb_12', 'emb_13', 'emb_14', 'emb_15', 'emb_16', 'emb_17', 'emb_18', 'emb_19', 'emb_20', 'emb_21', 'emb_22', 'emb_23', 'emb_24', 'emb_25', 'emb_26', 'emb_27', 'emb_28', 'emb_29', 'emb_30', 'emb_31', 'emb_32', 'emb_33', 'emb_34', 'emb_35', 'emb_36', 'emb_37', 'emb_38', 'emb_39', 'emb_40', 'emb_41', 'emb_42', 'emb_43', 'emb_44', 'e

In [315]:
df = df[columns_for_ML]
df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 530 entries, 0 to 1088
Columns: 249 entries, Bandgap, eV to Cell material_quartz
dtypes: bool(24), float64(225)
memory usage: 948.2 KB


In [316]:
df["Valence Electrons Density avg"] = df["Valence Electrons Density avg"].fillna(df["Valence Electrons Density avg"].mean())
df["Oxygen_concentration avg"] = df["Oxygen_concentration avg"].fillna(df["Oxygen_concentration avg"].mean())
df["Packing fraction avg"] = df["Packing fraction avg"].fillna(df["Packing fraction avg"].mean())

In [317]:

features_to_remove=['Oxygen_concentration avg','Valence electrons']
df = df.drop(columns=features_to_remove)

In [318]:
print(df.isna().sum().sum())
if(df.isna().sum().sum() != 0):
  print(df.isna().sum())
  raise StopExecution()


0


In [319]:
features = list(df.columns)
features.remove('Log_rate')

for f in features:
  print(f)

Bandgap, eV
d,A
CalcT(K)
Calc time (h)
Nitrogen
Promoter, w%
Surface area, m2/g
CatW, g/L
Alcohol, %
Power, W
Wave length min, nm
Temperature, K
avg s valence electrons
avg p valence electrons
avg d valence electrons
avg f valence electrons
frac s valence electrons
frac p valence electrons
frac d valence electrons
frac f valence electrons
Average Mulliken electronegativity
Valence Electrons Density avg
Packing fraction avg
emb_0
emb_1
emb_2
emb_3
emb_4
emb_5
emb_6
emb_7
emb_8
emb_9
emb_10
emb_11
emb_12
emb_13
emb_14
emb_15
emb_16
emb_17
emb_18
emb_19
emb_20
emb_21
emb_22
emb_23
emb_24
emb_25
emb_26
emb_27
emb_28
emb_29
emb_30
emb_31
emb_32
emb_33
emb_34
emb_35
emb_36
emb_37
emb_38
emb_39
emb_40
emb_41
emb_42
emb_43
emb_44
emb_45
emb_46
emb_47
emb_48
emb_49
emb_50
emb_51
emb_52
emb_53
emb_54
emb_55
emb_56
emb_57
emb_58
emb_59
emb_60
emb_61
emb_62
emb_63
emb_64
emb_65
emb_66
emb_67
emb_68
emb_69
emb_70
emb_71
emb_72
emb_73
emb_74
emb_75
emb_76
emb_77
emb_78
emb_79
emb_80
emb_81
emb_82
em

## Late outlier detection


In [320]:
if(remove_outliers_after_descriptors and remove_outliers):
  #raise SystemExit("Stopping execution")
  from sklearn.preprocessing import RobustScaler
  print(df.shape[0])
  scaler = RobustScaler()

  df_scaled = df.copy()
  df_scaled[features] = scaler.fit_transform(df[features])
  print(df.shape[0])
  df = df_scaled
else:
  print('Did nothing')

Did nothing


In [321]:
if(remove_outliers_after_descriptors and remove_outliers):
  #from sklearn.decomposition import PCA

  print(df.shape[0])

  X = df_scaled[features]

  #pca = PCA(n_components=0.95, random_state=0)
  #X_pca = pca.fit_transform(X)

  dist = np.linalg.norm(X, axis=1)


  threshold = np.percentile(dist, 80)
  print('Treshold = ',threshold)
  #threshold = X.std()
  #print('Treshold = ',threshold)
  df_clean = df[dist < threshold]

  print(df_clean.shape[0])
  df_clean.info()
  df = df_clean
else:
  print('Did nothing')

Did nothing


##Normalization

In [322]:
df.info()

<class 'pandas.core.frame.DataFrame'>
Index: 530 entries, 0 to 1088
Columns: 247 entries, Bandgap, eV to Cell material_quartz
dtypes: bool(24), float64(223)
memory usage: 939.9 KB


In [323]:
from sklearn.preprocessing import MinMaxScaler


scaler = MinMaxScaler()

df_normalized = df.copy()
df_normalized[features] = scaler.fit_transform(df_normalized[features])
df_normalized.head()

Bandgap, eV       d,A  CalcT(K)  Calc time (h)  Nitrogen  Promoter, w%  \
0     0.583333  0.484195  0.833333       0.239049       0.0           0.0   
1     0.458333  0.309483  0.833333       0.239049       0.0           0.0   
2     0.520833  0.315776  0.833333       0.239049       0.0           0.0   
3     0.500000  0.321408  0.833333       0.239049       0.0           0.0   
4     0.520833  0.423362  0.833333       0.239049       0.0           0.0   

   Surface area, m2/g  CatW, g/L  Alcohol, %  Power, W  ...  Promoter_NiO  \
0            0.091005   0.567117    0.429429     0.875  ...           0.0   
1            0.091005   0.567117    0.429429     0.875  ...           0.0   
2            0.091005   0.567117    0.429429     0.875  ...           0.0   
3            0.091005   0.567117    0.429429     0.875  ...           0.0   
4            0.091005   0.567117    0.429429     0.875  ...           0.0   

   Promoter_No promoter  Promoter_Pt  Promoter_Rh  Promoter_RuO2  \
0                   1.0          0.0          0.0            0.0   
1                   1.0          0.0          0.0            0.0   
2                   1.0          0.0          0.0            0.0   
3                   1.0          0.0          0.0            0.0   
4                   1.0          0.0          0.0            0.0   

   Promoter_ZnO  Light type_LED  Light type_W lamp   Light type_Xe lamp  \
0           0.0             0.0                 0.0                 0.0   
1           0.0             0.0                 0.0                 0.0   
2           0.0             0.0                 0.0                 0.0   
3           0.0             0.0                 0.0                 0.0   
4           0.0             0.0                 0.0                 0.0   

   Cell material_quartz  
0                   1.0  
1                   1.0  
2                   1.0  
3                   1.0  
4                   1.0  

[5 rows x 247 columns]

In [324]:
draw_corr_heatmap(df_normalized)

##Removing correlated features

In [325]:
var = df_normalized.var()
df_normalized = df_normalized.loc[:, var > 1e-8]

print(df_normalized.info())

corr = df_normalized.corr().abs()
upper = corr.where(np.triu(np.ones(corr.shape), k=1).astype(bool))
to_drop = [c for c in upper.columns if any(upper[c] > 0.95)]
df_normalized = df_normalized.drop(columns=to_drop)
print('Mutual correlation')
print(df_normalized.info())

<class 'pandas.core.frame.DataFrame'>
Index: 530 entries, 0 to 1088
Columns: 240 entries, Bandgap, eV to Cell material_quartz
dtypes: float64(240)
memory usage: 997.9 KB
None
Mutual correlation
<class 'pandas.core.frame.DataFrame'>
Index: 530 entries, 0 to 1088
Columns: 108 entries, Bandgap, eV to Cell material_quartz
dtypes: float64(108)
memory usage: 451.3 KB
None


In [326]:
draw_corr_heatmap(df_normalized)

#XY Split

In [327]:
X = df_normalized.drop(columns=[target_col])
y = df_normalized[target_col]

In [328]:
df_normalized.info()

<class 'pandas.core.frame.DataFrame'>
Index: 530 entries, 0 to 1088
Columns: 108 entries, Bandgap, eV to Cell material_quartz
dtypes: float64(108)
memory usage: 451.3 KB


In [329]:
df_normalized.to_excel('df_normalized.xlsx')

#Features selection

In [330]:
subset_cols = X.filter(like="emb_").columns.tolist()
print(subset_cols)

['emb_5', 'emb_6', 'emb_7', 'emb_9', 'emb_10', 'emb_12', 'emb_13', 'emb_14', 'emb_16', 'emb_17', 'emb_18', 'emb_19', 'emb_20', 'emb_22', 'emb_23', 'emb_24', 'emb_25', 'emb_26', 'emb_27', 'emb_28', 'emb_29', 'emb_30', 'emb_31', 'emb_32', 'emb_33', 'emb_34', 'emb_35', 'emb_36', 'emb_37', 'emb_38', 'emb_39', 'emb_40', 'emb_42', 'emb_43', 'emb_44', 'emb_45', 'emb_46', 'emb_47', 'emb_48', 'emb_49', 'emb_50', 'emb_51', 'emb_52', 'emb_53', 'emb_55', 'emb_56', 'emb_57', 'emb_58', 'emb_61', 'emb_63', 'emb_64', 'emb_65', 'emb_66', 'emb_67', 'emb_68', 'emb_70', 'emb_73', 'emb_74', 'emb_77', 'emb_78', 'emb_82', 'emb_83', 'emb_90']


In [331]:
from sklearn.decomposition import PCA

n_comp =30

#raise SystemExit("Stopping execution")

pca = PCA(n_components=n_comp, random_state=0)

if(do_PCA):
  columns_for_PCA = X.columns
  if(do_PCA_on_embeddings_only):
    columns_for_PCA = []
    columns_for_PCA = X.filter(like="emb_").columns.tolist()


  X_for_pca = X[columns_for_PCA]
  X_pca = pca.fit_transform(X_for_pca)
  explained = np.cumsum(pca.explained_variance_ratio_)
  plt.plot(explained, marker="o")
  plt.xlabel("Number of components")
  plt.ylabel("Cumulative explained variance")
  plt.grid()

  loadings = pd.DataFrame(
    pca.components_.T,
    columns=[f"PC{i+1}" for i in range(pca.n_components_)],
    index=X_for_pca.columns
  )
  X_for_pca.to_excel("checkpoint_X_before_PCA.xlsx")

  print(loadings)
  loadings.to_excel('PCA_loadings.xlsx')

  columns_after_PCA = [f'PC{i+1}' for i in range(pca.n_components_)]
  X_pca = pd.DataFrame(
      pca.fit_transform(X_for_pca),
      columns=columns_after_PCA,
      index=df.index
  )

  X_pca[columns_after_PCA] = scaler.fit_transform(X_pca[columns_after_PCA])

  df_pca = pd.concat([X_pca, y], axis=1)
  X = pd.concat([X, X_pca], axis=1)
  X = X.drop(columns_for_PCA, axis=1)
  df_pca.to_excel("checkpoint_ML_input.xlsx")
  X_pca.to_excel("checkpoint_X_after_PCA.xlsx")

#X_val_pca = pca.transform(scaler.transform(X_val))
#X_pca.info()
else:
  print('Do nothing')

Do nothing


In [332]:
X.describe()

Bandgap, eV         d,A    CalcT(K)  Calc time (h)    Nitrogen  \
count   530.000000  530.000000  530.000000     530.000000  530.000000   
mean      0.567847    0.421457    0.686015       0.083627    0.020755   
std       0.156306    0.211115    0.166540       0.085489    0.142697   
min       0.000000    0.000000    0.000000       0.000000    0.000000   
25%       0.500000    0.349131    0.625000       0.048811    0.000000   
50%       0.562500    0.405076    0.750000       0.058824    0.000000   
75%       0.616667    0.494684    0.791667       0.097539    0.000000   
max       1.000000    1.000000    1.000000       1.000000    1.000000   

       Promoter, w%  Surface area, m2/g   CatW, g/L  Alcohol, %    Power, W  \
count    530.000000          530.000000  530.000000  530.000000  530.000000   
mean       0.103532            0.118432    0.233456    0.126234    0.395637   
std        0.148680            0.153804    0.177281    0.214202    0.371371   
min        0.000000            0.000000    0.000000    0.000000    0.000000   
25%        0.000000            0.043985    0.093966    0.000000    0.062500   
50%        0.020000            0.091005    0.194636    0.030030    0.062500   
75%        0.200000            0.091005    0.395977    0.162162    0.750000   
max        1.000000            1.000000    1.000000    1.000000    1.000000   

       ...  Promoter_Ni  Promoter_NiO  Promoter_No promoter  Promoter_Pt  \
count  ...   530.000000    530.000000            530.000000   530.000000   
mean   ...     0.001887      0.181132              0.413208     0.358491   
std    ...     0.043437      0.385491              0.492875     0.480010   
min    ...     0.000000      0.000000              0.000000     0.000000   
25%    ...     0.000000      0.000000              0.000000     0.000000   
50%    ...     0.000000      0.000000              0.000000     0.000000   
75%    ...     0.000000      0.000000              1.000000     1.000000   
max    ...     1.000000      1.000000              1.000000     1.000000   

       Promoter_Rh  Promoter_ZnO  Light type_LED  Light type_W lamp   \
count   530.000000    530.000000      530.000000          530.000000   
mean      0.007547      0.003774        0.003774            0.001887   
std       0.086628      0.061371        0.061371            0.043437   
min       0.000000      0.000000        0.000000            0.000000   
25%       0.000000      0.000000        0.000000            0.000000   
50%       0.000000      0.000000        0.000000            0.000000   
75%       0.000000      0.000000        0.000000            0.000000   
max       1.000000      1.000000        1.000000            1.000000   

       Light type_Xe lamp  Cell material_quartz  
count          530.000000            530.000000  
mean             0.092453              0.905660  
std              0.289938              0.292577  
min              0.000000              0.000000  
25%              0.000000              1.000000  
50%              0.000000              1.000000  
75%              0.000000              1.000000  
max              1.000000              1.000000  

[8 rows x 107 columns]

#ML


In [333]:
#raise SystemExit("Stopping execution")


print('Std:',y.std())

print(X.shape)

Std: 3.1847827785492053
(530, 107)


In [334]:
from sklearn.model_selection import train_test_split
from sklearn.preprocessing import StandardScaler
from sklearn.impute import SimpleImputer
from sklearn.linear_model import LinearRegression
from sklearn.metrics import mean_squared_error, r2_score
from sklearn.model_selection import cross_val_score
from sklearn.metrics import make_scorer, mean_squared_error
from sklearn.model_selection import cross_val_predict
from sklearn.model_selection import KFold

In [335]:
X_train, X_test, y_train, y_test = train_test_split(
    X, y, test_size=0.2, shuffle=True
)


In [336]:
if(do_LASSO):
  from sklearn.linear_model import Lasso
  from sklearn.linear_model import LassoCV

  lasso_cv = LassoCV(cv=5, max_iter=10000)
  lasso_cv.fit(X_train, y_train)
  print("Optimal alpha:", lasso_cv.alpha_)

  # Use the selected alpha
  lasso_best = Lasso(alpha=lasso_cv.alpha_)
  lasso_best.fit(X_train, y_train)


  #lasso = Lasso(alpha=0.01, max_iter=10000)
  #lasso.fit(X_train, y_train)
  coef = pd.Series(lasso_best.coef_, index=X.columns)

  # Selected features (non-zero coefficients)
  selected_features = coef[coef != 0].index.tolist()
  print("Selected features:", selected_features)
  print("Values: ",coef[coef != 0])
  print(len(selected_features))
  X = X[selected_features]
  X_train, X_test, y_train, y_test = train_test_split(
    X, y, test_size=0.2, shuffle=True
  )
  print(X.shape)
else:
  print("Do nothing")

/usr/local/lib/python3.12/dist-packages/sklearn/linear_model/_coordinate_descent.py:681: ConvergenceWarning:

Objective did not converge. You might want to increase the number of iterations. Duality gap: 0.45219268549533354, tolerance: 0.34142899709201874

/usr/local/lib/python3.12/dist-packages/sklearn/linear_model/_coordinate_descent.py:681: ConvergenceWarning:

Objective did not converge. You might want to increase the number of iterations. Duality gap: 0.5162943815508925, tolerance: 0.34375164721024437

/usr/local/lib/python3.12/dist-packages/sklearn/linear_model/_coordinate_descent.py:681: ConvergenceWarning:

Objective did not converge. You might want to increase the number of iterations. Duality gap: 0.5656006035554242, tolerance: 0.34375164721024437

/usr/local/lib/python3.12/dist-packages/sklearn/linear_model/_coordinate_descent.py:681: ConvergenceWarning:

Objective did not converge. You might want to increase the number of iterations. Duality gap: 0.5906068974903746, toleran

Optimal alpha: 0.0024179669493573494
Selected features: ['Bandgap, eV', 'd,A', 'CalcT(K)', 'Calc time (h)', 'Nitrogen', 'CatW, g/L', 'Alcohol, %', 'Power, W', 'Wave length min, nm', 'Temperature, K', 'avg s valence electrons', 'avg f valence electrons', 'frac s valence electrons', 'frac p valence electrons', 'frac d valence electrons', 'Average Mulliken electronegativity', 'Valence Electrons Density avg', 'emb_6', 'emb_9', 'emb_10', 'emb_13', 'emb_16', 'emb_17', 'emb_19', 'emb_22', 'emb_23', 'emb_26', 'emb_27', 'emb_28', 'emb_29', 'emb_31', 'emb_32', 'emb_35', 'emb_39', 'emb_40', 'emb_44', 'emb_47', 'emb_48', 'emb_49', 'emb_53', 'emb_55', 'emb_63', 'emb_66', 'emb_68', 'emb_70', 'emb_73', 'emb_78', 'emb_83', 'Prep Method_MSS', 'Prep Method_PC', 'Prep Method_PTP', 'Prep Method_SG', 'Prep Method_purchased', 'Promotion method_PD', 'Promotion method_impregnation', 'Promoter_CuO', 'Promoter_Fe2O3', 'Promoter_Ni', 'Promoter_NiO', 'Promoter_Pt', 'Promoter_Rh', 'Light type_LED', 'Light type_W l

/usr/local/lib/python3.12/dist-packages/sklearn/linear_model/_coordinate_descent.py:695: ConvergenceWarning:

Objective did not converge. You might want to increase the number of iterations, check the scale of the features or consider increasing regularisation. Duality gap: 6.814e+01, tolerance: 4.224e-01



In [337]:
#y_pred = lasso.predict(X_test)
#print("Test R²:", r2_score(y_test, y_pred))

In [338]:
def draw_actual_predicted(_y_test, _y_pred):
  fig = px.scatter(
    x=_y_test,
    y=_y_pred,
    labels={'x':'Actual', 'y':'Predicted'},
    title='Actual vs Predicted',
    width = 700,
    height = 700,
  )
  fig.add_shape(
      type="line",
      #x0=_y_test.min(), y0=_y_pred.min(),
      #x1=_y_test.max(), y1=_y_pred.max(),
      x0=-5, y0=-5,
      x1=12, y1=12,
      line=dict(color="red", dash="dash")
  )
  rmse = np.sqrt(mean_squared_error(_y_test, _y_pred))
  r2 = r2_score(_y_test, _y_pred)

  fig.add_annotation(
    x=0.05, y=0.95, xref="paper", yref="paper",
    text=f"R² = {r2:.4f}<br>RMSE = {rmse:.4f}",
    showarrow=False,
    font=dict(size=14)
  )
  fig.show()

##Linear regression

In [339]:
linear_model = LinearRegression()

if(cross_validation):
  cv = KFold(n_splits=5, shuffle=True)
  scores = cross_val_score(linear_model, X, y, cv=cv, scoring='neg_mean_squared_error')
  rmse_scores = np.sqrt(-scores)
  print("Scores: ", scores)
  print("Mean RMSE:", rmse_scores.mean())

  y_pred = cross_val_predict(linear_model, X, y, cv=5)
  draw_actual_predicted(y, y_pred)
else:
  print('No cross validation')
  linear_model.fit(X_train, y_train)
  y_pred = linear_model.predict(X_test)
  draw_actual_predicted(y_test, y_pred)

Scores:  [-3.06306845 -4.09594201 -3.61943611 -2.1679313  -2.94311423]
Mean RMSE: 1.7728855422651182


In [340]:
def estimate_performance(_y_test, _y_pred):
  raisemse = np.sqrt(mean_squared_error(_y_test, _y_pred))
  r2 = r2_score(_y_test, _y_pred)

  print("RMSE:", mse)
  print("R² Score:", r2)

##Decision tree regression

In [341]:
from sklearn.tree import DecisionTreeRegressor

In [342]:
tree_model = DecisionTreeRegressor(random_state=42)

if(cross_validation):
  scores = cross_val_score(tree_model, X, y, cv=5, scoring='neg_mean_squared_error')
  rmse_scores = np.sqrt(-scores)
  print("Scores: ", scores)
  print("Mean RMSE:", rmse_scores.mean())

  y_pred = cross_val_predict(tree_model, X, y, cv=5)
  draw_actual_predicted(y, y_pred)
else:
  print('No cross validation')
  tree_model.fit(X_train, y_train)
  y_pred = tree_model.predict(X_test)
  draw_actual_predicted(y_test, y_pred)

Scores:  [ -9.77805944 -13.86011188 -17.40429631  -4.79419975  -5.21896286]
Mean RMSE: 3.099164545286205


In [343]:
import matplotlib.pyplot as plt

if not(cross_validation):
  feat_imp = pd.DataFrame({
      'Feature': X.columns,
      'Importance': tree_model.feature_importances_
  }).sort_values(by='Importance', ascending=False)

  plt.figure(figsize=(8,6))
  sns.barplot(x='Importance', y='Feature', data=feat_imp)
  plt.title('Feature Importance')
  plt.show()

## Random forest

In [344]:
from sklearn.ensemble import RandomForestRegressor

In [345]:
rf_model = RandomForestRegressor(
    n_estimators=100,
    max_depth=5,
    min_samples_split = 10,
    min_samples_leaf = 1,
    max_features=2,
    random_state=42
)

if(cross_validation):
  scores = cross_val_score(rf_model , X, y, cv=5, scoring='neg_mean_squared_error')
  rmse_scores = np.sqrt(-scores)
  print("Scores: ", scores)
  print("Mean RMSE:", rmse_scores.mean())

  y_pred = cross_val_predict(rf_model , X, y, cv=5)
  draw_actual_predicted(y, y_pred)
else:
  print('No cross validation')
  rf_model.fit(X_train, y_train)
  y_pred = rf_model.predict(X_test)
  draw_actual_predicted(y_test, y_pred)

Scores:  [-7.44990533 -6.06218318 -7.18484991 -8.26848882 -6.49258215]
Mean RMSE: 2.6591222419888707


In [346]:
if not(cross_validation):
  feat_imp = pd.DataFrame({
      'Feature': X.columns,
      'Importance': rf_model.feature_importances_
  }).sort_values(by='Importance', ascending=False)

  plt.figure(figsize=(8,6))
  sns.barplot(x='Importance', y='Feature', data=feat_imp)
  plt.title('Feature Importance')
  plt.show()

In [347]:
from sklearn.model_selection import GridSearchCV

if(grid_search):
  param_grid = {
      'n_estimators': [50, 100, 150],
      'max_depth': [4, 5],
      'min_samples_split': [5, 10],
      'min_samples_leaf': [1, 2],
  }
  #Best params {'max_depth': 5, 'min_samples_leaf': 1, 'min_samples_split': 10, 'n_estimators': 100}
  #Best params {'max_depth': 5, 'min_samples_leaf': 1, 'min_samples_split': 10, 'n_estimators': 100}
  #Best params {'max_depth': 5, 'min_samples_leaf': 2, 'min_samples_split': 10, 'n_estimators': 100}

  grid_search = GridSearchCV(RandomForestRegressor(random_state=42),
                            param_grid, cv=5, scoring='neg_mean_squared_error')
  grid_search.fit(X,y)
  print('Best params',grid_search.best_params_)
  print('Best score',grid_search.best_score_)

In [348]:
if(grid_search):
  best_model = grid_search.best_estimator_

  if(cross_validation):
    scores = cross_val_score(best_model , X, y, cv=5, scoring='neg_mean_squared_error')
    rmse_scores = np.sqrt(-scores)
    print("Scores: ", scores)
    print("Mean RMSE:", rmse_scores.mean())

    y_pred = cross_val_predict(best_model , X, y, cv=5)
    draw_actual_predicted(y, y_pred)
  else:
    y_pred = best_model.predict(X_test)
    draw_actual_predicted(y_test, y_pred)

##Gradient boosting

In [349]:
from sklearn.ensemble import GradientBoostingRegressor

In [350]:
gb_model = GradientBoostingRegressor(
    n_estimators=100,      # number of boosting stages
    learning_rate=0.1,     # shrinkage factor
    max_depth=4,           # depth of each tree
    min_samples_split=6,
    min_samples_leaf=2,
    random_state=42,
    subsample=0.8
)

if(cross_validation):
  scores = cross_val_score(gb_model , X, y, cv=5, scoring='neg_mean_squared_error')
  rmse_scores = np.sqrt(-scores)
  print("Scores: ", scores)
  print("Mean RMSE:", rmse_scores.mean())

  y_pred = cross_val_predict(gb_model , X, y, cv=5)
  draw_actual_predicted(y, y_pred)
else:
  gb_model.fit(X_train, y_train)
  y_pred = gb_model.predict(X_test)
  draw_actual_predicted(y_test, y_pred)

Scores:  [-7.93392566 -7.47592915 -6.2564103  -4.51289866 -3.94279168]
Mean RMSE: 2.43244471988534


In [351]:
if not(cross_validation):
  feat_imp = pd.DataFrame({
      'Feature': X.columns,
      'Importance': gb_model.feature_importances_
  }).sort_values(by='Importance', ascending=False)

  plt.figure(figsize=(8,6))
  sns.barplot(x='Importance', y='Feature', data=feat_imp)
  plt.title('Feature Importance')
  plt.show()

In [352]:
if(grid_search):
  param_grid = {
      'n_estimators': [100, 150],        # number of boosting stages
      'learning_rate': [0.01, 0.1],   # shrinkage factor
      'max_depth': [3, 4],                # depth of each tree
      'min_samples_split': [4, 6],
      'min_samples_leaf': [1, 2, 3],
      'subsample': [0.8, 1.0]                # fraction of samples for each tree
  }
  #Best parameters: {'learning_rate': 0.1, 'max_depth': 4, 'min_samples_leaf': 2, 'min_samples_split': 6, 'n_estimators': 100, 'subsample': 0.8}
  #Best parameters: {'learning_rate': 0.1, 'max_depth': 4, 'min_samples_leaf': 2, 'min_samples_split': 6, 'n_estimators': 100, 'subsample': 0.8}
  #Best parameters: {'learning_rate': 0.1, 'max_depth': 4, 'min_samples_leaf': 1, 'min_samples_split': 4, 'n_estimators': 100, 'subsample': 0.8}

  # Grid search with 5-fold cross-validation
  grid_search = GridSearchCV(
      estimator=gb_model,
      param_grid=param_grid,
      cv=5,
      scoring='neg_mean_squared_error',          # or 'neg_mean_squared_error'
      n_jobs=-1,
      verbose=2
  )

  # Fit on training data
  grid_search.fit(X, y)

  # Best hyperparameters
  print("Best parameters:", grid_search.best_params_)
  print("Best CV RMSE:", grid_search.best_score_)

In [353]:
if(grid_search):
  best_model = grid_search.best_estimator_

  if(cross_validation):
    scores = cross_val_score(best_model , X, y, cv=5, scoring='neg_mean_squared_error')
    rmse_scores = np.sqrt(-scores)
    print("Scores: ", scores)
    print("Mean RMSE:", rmse_scores.mean())

    y_pred = cross_val_predict(best_model , X, y, cv=5)
    draw_actual_predicted(y, y_pred)
  else:
    y_pred = best_model.predict(X_test)
    draw_actual_predicted(y_test, y_pred)

##KNN

In [354]:
from sklearn.neighbors import KNeighborsRegressor

In [355]:
knn_model = KNeighborsRegressor(n_neighbors=20, weights='uniform',p=1)

if(cross_validation):
  scores = cross_val_score(knn_model , X, y, cv=5, scoring='neg_mean_squared_error')
  rmse_scores = np.sqrt(-scores)
  print("Scores: ", scores)
  print("Mean RMSE:", rmse_scores.mean())

  y_pred = cross_val_predict(knn_model , X, y, cv=5)
  draw_actual_predicted(y, y_pred)
else:
  knn_model.fit(X_train, y_train)
  y_pred = knn_model.predict(X_test)
  draw_actual_predicted(y_test, y_pred)

Scores:  [-8.05165776 -5.67239866 -7.13266878 -3.54566157 -5.22322962]
Mean RMSE: 2.4116722219186597


In [356]:
if(grid_search):
  param_grid = {
      'n_neighbors': list(range(1, 21)),
      'weights': ['uniform', 'distance'],
      'p': [1, 2]
  }
  #Best parameters: {'n_neighbors': 20, 'p': 1, 'weights': 'uniform'}
  #Best parameters: {'n_neighbors': 20, 'p': 1, 'weights': 'uniform'}
  #Best parameters: {'n_neighbors': 12, 'p': 2, 'weights': 'distance'}

  grid_search = GridSearchCV(
      KNeighborsRegressor(),
      param_grid,
      cv=5,
      scoring='neg_mean_squared_error',
      n_jobs=-1,
      verbose=2
  )

  grid_search.fit(X,y)

  print("Best parameters:", grid_search.best_params_)
  print("Best CV RMSE:", grid_search.best_score_)

In [357]:
if(grid_search):
  best_model = grid_search.best_estimator_

  if(cross_validation):
    scores = cross_val_score(best_model , X, y, cv=5, scoring='neg_mean_squared_error')
    rmse_scores = np.sqrt(-scores)
    print("Scores: ", scores)
    print("Mean RMSE:", rmse_scores.mean())

    y_pred = cross_val_predict(best_model , X, y, cv=5)
    draw_actual_predicted(y, y_pred)
  else:
    y_pred = best_model.predict(X_test)
    draw_actual_predicted(y_test, y_pred)

##Catboost

In [358]:
from catboost import CatBoostRegressor

In [359]:
cat_boost_model = CatBoostRegressor(
    iterations=1000,
    learning_rate=0.05,
    depth=4,
    verbose=100
)

if(cross_validation):
  scores = cross_val_score(cat_boost_model , X, y, cv=5, scoring='neg_mean_squared_error')
  rmse_scores = np.sqrt(-scores)
  print("Scores: ", scores)
  print("Mean RMSE:", rmse_scores.mean())

  y_pred = cross_val_predict(cat_boost_model , X, y, cv=5)
  draw_actual_predicted(y, y_pred)
else:
  cat_boost_model.fit(X_train, y_train)
  y_pred = cat_boost_model.predict(X_test)
  draw_actual_predicted(y_test, y_pred)

0:	learn: 3.0864573	total: 2.7ms	remaining: 2.7s
100:	learn: 1.3336966	total: 139ms	remaining: 1.23s
200:	learn: 1.0259864	total: 477ms	remaining: 1.9s
300:	learn: 0.8649358	total: 920ms	remaining: 2.14s
400:	learn: 0.7487156	total: 1.34s	remaining: 2.01s
500:	learn: 0.6627105	total: 1.66s	remaining: 1.65s
600:	learn: 0.5989800	total: 2.06s	remaining: 1.37s
700:	learn: 0.5484529	total: 2.47s	remaining: 1.05s
800:	learn: 0.5146593	total: 2.84s	remaining: 706ms
900:	learn: 0.4898357	total: 3.24s	remaining: 356ms
999:	learn: 0.4681999	total: 3.65s	remaining: 0us
0:	learn: 3.1019176	total: 3.07ms	remaining: 3.06s
100:	learn: 1.4688832	total: 408ms	remaining: 3.63s
200:	learn: 1.0885320	total: 588ms	remaining: 2.34s
300:	learn: 0.8884932	total: 728ms	remaining: 1.69s
400:	learn: 0.7709225	total: 867ms	remaining: 1.29s
500:	learn: 0.6767592	total: 1.01s	remaining: 1s
600:	learn: 0.6043803	total: 1.15s	remaining: 763ms
700:	learn: 0.5579676	total: 1.29s	remaining: 550ms
800:	learn: 0.5215399	

In [360]:
if(grid_search):
  param_grid = {
      'depth': [4,6],
      'learning_rate':[0.01,0.05,0.1 ]
  }
  #Best parameters: {'depth': 4, 'learning_rate': 0.05}
  #Best parameters: {'depth': 4, 'learning_rate': 0.05}
  #Best parameters: {'depth': 6, 'learning_rate': 0.05}

  grid_search = GridSearchCV(cat_boost_model, param_grid, cv=5,scoring='neg_mean_squared_error',)
  grid_search.fit(X,y)

  print("Best parameters:", grid_search.best_params_)
  print("Best CV RMSE:", grid_search.best_score_)

In [361]:
if(grid_search):
  est_model = grid_search.best_estimator_

  if(cross_validation):
    print("Cross validation")
    scores = cross_val_score(best_model , X, y, cv=5, scoring='neg_mean_squared_error')
    rmse_scores = np.sqrt(-scores)

    y_pred = cross_val_predict(best_model , X, y, cv=5)
    draw_actual_predicted(y, y_pred)
    print("Scores: ", scores)
    print("Mean RMSE:", rmse_scores.mean())
  else:
    y_pred = best_model.predict(X_test)
    draw_actual_predicted(y_test, y_pred)

##XGBoost

In [362]:
import xgboost as xgb
from xgboost import XGBRegressor

In [363]:
xgboost_model = XGBRegressor(
    n_estimators=300,
    max_depth=4,
    learning_rate=0.05,
    subsample=0.8,
    colsample_bytree=0.8,
    random_state=42
)

In [364]:
if(cross_validation):
  scores = cross_val_score(xgboost_model , X, y, cv=5, scoring='neg_mean_squared_error')
  rmse_scores = np.sqrt(-scores)
  print("Scores: ", scores)
  print("Mean RMSE:", rmse_scores.mean())

  y_pred = cross_val_predict(xgboost_model , X, y, cv=5)
  draw_actual_predicted(y, y_pred)
else:
  xgboost_model.fit(X_train, y_train)
  y_pred = xgboost_model.predict(X_test)
  draw_actual_predicted(y_test, y_pred)

Scores:  [-7.24611938 -5.85770385 -5.55566627 -4.52318883 -3.4321648 ]
Mean RMSE: 2.2897132810875025


In [365]:
X_Maliken = X[['Average Mulliken electronegativity']]

if(cross_validation):
  cv = KFold(n_splits=5, shuffle=True)
  scores = cross_val_score(linear_model, X_Maliken, y, cv=cv, scoring='neg_mean_squared_error')
  rmse_scores = np.sqrt(-scores)
  print("Scores: ", scores)
  print("Mean RMSE:", rmse_scores.mean())

  y_pred = cross_val_predict(linear_model, X_Maliken, y, cv=5)
  draw_actual_predicted(y, y_pred)
else:
  print('No cross validation')
  linear_model.fit(X_train, y_train)
  y_pred = linear_model.predict(X_test)
  draw_actual_predicted(y_test, y_pred)

Scores:  [-9.18245241 -7.34930726 -8.99183477 -7.83331659 -7.0093248 ]
Mean RMSE: 2.837234957277206
